## Домашнее задание

Основаная задача - **построить хорошую тематическую модель с интерпретируемыми топиками с помощью LDA в gensim и NMF в sklearn**.


1) сделайте нормализацию (если pymorphy2 работает долго используйте mystem или попробуйте установить быструю версию - `pip install pymorphy2[fast]`, можно использовать какой-то другой токенизатор); 

2) добавьте нграммы (в тетрадке есть закомменченая ячейка с Phrases,  можно также попробовать другие способы построить нграммы); 

3) сделайте хороший словарь (отфильтруйте слишком частотные и редкие слова, попробуйте удалить стоп-слова); 

4) постройте несколько LDA моделей (переберите количество тем, можете поменять eta, alpha, passes), если получаются плохие темы, поработайте дополнительно над предобработкой и словарем; 

5) для самой хорошей модели в отдельной ячейке напечатайте 3 хороших (на ваш вкус) темы;

6) между словарем и обучением модели добавьте tfidf (`gensim.models.TfidfModel(corpus, id2word=dictionary); corpus = tfidf[corpus]`);

7) повторите пункт 4 на преобразованном корпусе;

8) в отдельной ячейке опишите как изменилась модель (приведите несколько тем, которые стали лучше или хуже, или которых раньше вообще не было; можно привести значения перплексии и когерентности для обеих моделей)

9) проделайте такие же действия для NMF (образец в конце тетрадки), для построения словаря воспользуйтесь возможностями Count или Tfidf Vectorizer (попробуйте другие значение max_features, min_df, max_df, сделайте нграмы через ngram_range, если хватает памяти), попробуйте такие же количества тем

10) в отдельной ячейки напечатайте таблицу с темами лучшей NMF модели, сравните их с теми, что получились в LDA.

Сохраните тетрадку с экспериментами и положите её на гитхаб, ссылку на неё укажите в форме.

**Оцениваться будут главным образом пункты 5, 8 и 10. (2, 3, 2 баллов соответственно). Чтобы заработать остальные 3 балла, нужно хотя бы немного изменить мой код на промежуточных этапах (добавить что-то, указать другие параметры и т.д). **

In [1]:
import gensim
import json
import re
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from pymorphy2 import MorphAnalyzer
import pyLDAvis.gensim
import string
from collections import Counter
import warnings
warnings.filterwarnings("ignore")

morph = MorphAnalyzer()

## Данные

In [2]:
stops = set(stopwords.words('russian')) | {'gt',} | set(stopwords.words('english'))
def remove_tags(text):
    return re.sub(r'<[^>]+>', '', text)

def normalize(words):
    norm_words = [morph.parse(word)[0].normal_form for word in words if len(set(word)) > 1]
    return norm_words

def opt_normalize(texts, top=None):
    uniq = Counter()
    for text in texts:
        uniq.update(text)
    
    norm_uniq = {word:morph.parse(word)[0].normal_form for word, _ in uniq.most_common(top)}
    
    norm_texts = []
    for text in texts:
        
        norm_words = [norm_uniq.get(word) for word in text]
        norm_words = [word for word in norm_words if word and word not in stops]
        norm_texts.append(norm_words)
        
    return norm_texts

def tokenize(text):
    words = [word.strip(string.punctuation) for word in text.split()]
    words = [word for word in words if word]
    
    return words

Возьмем 4 тыс статьи с Хабра. Это мало для хорошей тематической модели, но иначе у нас просто ничего не обучится за семинар.

В текстах есть тэги. Потрем их. Ещё токенизируем самым простым способом и нормализуем Pymorphy.

In [3]:
%%time
texts = open('habr_texts.txt').read().splitlines()
texts = [tokenize(remove_tags(text.lower())) for text in texts]

CPU times: user 4.23 s, sys: 524 ms, total: 4.76 s
Wall time: 5.48 s


In [4]:
%%time
texts = open('habr_texts.txt').read().splitlines()
texts = [normalize(tokenize(text.lower())) for text in texts]

CPU times: user 25min 48s, sys: 1.5 s, total: 25min 50s
Wall time: 30min 30s


In [5]:
%%time
texts = open('habr_texts.txt').read().splitlines()
texts = opt_normalize([tokenize(remove_tags(text.lower())) for text in texts], 30000)

CPU times: user 17.9 s, sys: 460 ms, total: 18.3 s
Wall time: 22.1 s


In [6]:
# для нграммов
ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
p = gensim.models.phrases.Phraser(ph)
ngrammed_texts = p[texts]

### Тематическое моделирование в gensim

Для моделей нужно сделать словарь.

In [6]:
dictinary = gensim.corpora.Dictionary(texts)

In [7]:
dictinary.filter_extremes(no_above=0.3)
dictinary.compactify()

In [8]:
print(dictinary)

Dictionary(12138 unique tokens: ['2-х', '3.0', 'address', 'api', 'architecture']...)


Преобразуем наши тексты в мешки слов. 

In [9]:
corpus = [dictinary.doc2bow(text) for text in texts]
# если текстов много, то тут может быть генератор

In [11]:
?gensim.models.LdaMulticore

In [ ]:
%%time
lda = gensim.models.LdaMulticore(corpus, 100, id2word=dictinary, passes=5, eta='auto', iterations=10) # если поддерживается многопоточность
# lsi = gensim.models.LdaModel(200, id2word=dictinary, passes=5)

In [10]:
def lda_mod(texts,
        no_above=0.3,
        ngrams=True,
        tfidf=False,
        passes=5,
        eta='auto', 
        iterations=10, 
        num_topics=100):
    if ngrams:
        ph = gensim.models.Phrases(texts, scoring='npmi', threshold=0.4) # threshold можно подбирать
        p = gensim.models.phrases.Phraser(ph)
        texts = p[texts]
    dictionary = gensim.corpora.Dictionary(texts)
    dictionary.filter_extremes(no_above=no_above)
    dictionary.compactify()
    
    corpus = [dictionary.doc2bow(text) for text in texts]
    if tfidf:
        tfidf = gensim.models.TfidfModel(corpus, id2word=dictionary)
        corpus = tfidf[corpus]
    lda_model = gensim.models.LdaModel(corpus=corpus, 
                                       id2word=dictionary,
                                       num_topics=num_topics,
                                       random_state=55,
                                       passes=passes,
                                       eta=eta, 
                                       iterations=iterations)
    return lda_model

In [12]:
%%time
lda_model = lda_mod(texts)

CPU times: user 3min 46s, sys: 2min 35s, total: 6min 22s
Wall time: 4min 10s


Посмотрим на топики.

In [13]:
lda_model.print_topics()

[(77,
  '0.090*"игра" + 0.032*"игрок" + 0.015*"играть" + 0.011*"игровой" + 0.009*"понять" + 0.007*"исследование" + 0.005*"дизайнер" + 0.005*"понимать" + 0.004*"почему" + 0.004*"что-то"'),
 (48,
  '0.032*"товар" + 0.014*"автор" + 0.013*"машина" + 0.013*"скидка" + 0.013*"аккумулятор" + 0.011*"день" + 0.011*"ключ" + 0.010*"apple" + 0.010*"зарядка" + 0.009*"автомобиль"'),
 (51,
  '0.029*"игрок" + 0.016*"удача" + 0.011*"игра" + 0.009*"видео" + 0.009*"очки" + 0.009*"автомат" + 0.008*"её" + 0.007*"корея" + 0.007*"вероятность" + 0.007*"костя"'),
 (37,
  '0.028*"прокси-сервер" + 0.020*"openmp" + 0.018*"cad" + 0.016*"squid" + 0.015*"docker_swarm" + 0.015*"parallel" + 0.014*"00_00" + 0.012*"microsoft_sql" + 0.011*"kubernetes" + 0.009*"распараллелить"'),
 (64,
  '0.006*"публикация" + 0.004*"мир" + 0.004*"действительно" + 0.004*"ресурс" + 0.003*"тема" + 0.003*"распространение" + 0.003*"месяц" + 0.003*"сообщество" + 0.003*"интерес" + 0.003*"день"'),
 (59,
  '0.102*"модуль" + 0.035*"ecto" + 0.034*"сп

плохо понятно, давайте сделаем таблицу!

In [14]:
import pandas as pd

In [15]:
res_bad = lda_model.print_topics()

res_good = []
for word in res_bad:
    res = re.findall('\*"(.*?)"', word[1])
    res_good.append(res)
pd.DataFrame(res_good).T

0            1             2         3          4   \
0     firebase         сайт    устройство      цикл    планета   
1       индекс         сеть        раздел  значение      земля   
2   интеграция       страна         режим  параметр      слово   
3      node.js     интернет      загрузка    вектор  программа   
4      выборка      продажа       выбрать        lt       луна   
5    поисковый       клиент          файл         x   астероид   
6  реализовать       трафик        флешек   элемент     pebble   
7          mvp  южный_корея  перезагрузка  алгоритм        ide   
8          var   посетитель     выполнить         4     солнце   
9       объект        канал          база  скорость     планет   

                 5               6              7          8   \
0               crm  инфраструктура           боль       игра   
1       crm-система          клиент              •   название   
2     сообщать_тасс        инцидент      изменение         её   
3    regionsoft_crm          доступ    определение      экран   
4     ит-специалист         правило           тело     движок   
5        regionsoft        implicit  сопротивление  компьютер   
6                sv            хост    происходить       лишь   
7          рекрутер      управление       ситуация  интерфейс   
8            круге»  учётный_запись        наличие      карта   
9  выглядеть_ужасно      требование       движение   редактор   

                      9            10                   11  \
0                  слово       доклад                  ибп   
1                   язык  конференция                blink   
2               лицензия   рассказать                  bmc   
3  язык_программирование         тема                   xe   
4                     ui  мероприятие  выходной_напряжение   
5             библиотека  выступление       электропитание   
6              платформа          фсб             дежурный   
7              свободный       спикер          электросеть   
8                   сайт         2017           напряжение   
9                 облако  презентация                 ipmi   

                         12          13           14      15               16  \
0                  viewport      модель        товар     new       публикация   
1                        м2      сервер        автор  public              мир   
2                         р   изменение       машина  return    действительно   
3                   elastic   компонент       скидка   метод           ресурс   
4  подтвердить_опровергнуть      клиент  аккумулятор  string             тема   
5                      метр      объект         день    null  распространение   
6                    wallet  реализация         ключ     var            месяц   
7                  менеджер       выбор        apple   класс       сообщество   
8                      гуру          3d      зарядка  объект          интерес   
9            торговый_марка  обновление   автомобиль    void             день   

            17          18         19  
0    двигатель    какой-то     дефект  
1      спутник      что-то     ошибка  
2  космический       книга  программа  
3      аппарат      вообще     вместо  
4      причина      читать  сравнение  
5     проверка      думать   значение  
6         пуск       ничто       язык  
7       запуск        день  выражение  
8       орбита  заниматься   привести  
9        полёт        идея   оператор

Ещё есть штука для визуализации.

In [22]:
pyLDAvis.enable_notebook()

In [24]:
pyLDAvis.gensim.prepare(lda_model, corpus, dictinary)

PreparedData(topic_coordinates=              x         y  topics  cluster      Freq
topic                                               
27    -0.143763  0.057318       1        1  4.661150
24     0.106322  0.035279       2        1  3.929522
1     -0.081905 -0.056384       3        1  3.324593
25     0.190277 -0.099304       4        1  3.152049
86    -0.115242 -0.058461       5        1  3.104139
32    -0.081205  0.002628       6        1  2.911200
84    -0.131603  0.050538       7        1  2.846290
47    -0.135294  0.050247       8        1  2.690173
71    -0.164471  0.021174       9        1  2.526308
22    -0.097122 -0.004306      10        1  2.394955
67    -0.129791  0.006714      11        1  2.367384
12     0.085702  0.027628      12        1  2.213985
40    -0.042179  0.072109      13        1  2.077639
65     0.219001  0.061143      14        1  2.004515
33     0.012743  0.030332      15        1  1.996951
56     0.130679  0.032062      16        1  1.927340
96    -0.100438  0.075965      17        1  1.691834
30    -0.138295  0.054679      18        1  1.684639
43     0.182010 -0.052134      19        1  1.611564
88    -0.121482  0.046579      20        1  1.547724
3     -0.115685  0.049844      21        1  1.445287
49    -0.072452 -0.008617      22        1  1.326038
54    -0.019939 -0.014487      23        1  1.263078
50    -0.040909  0.092465      24        1  1.247514
36    -0.053586  0.085983      25        1  1.210531
0     -0.018496 -0.093046      26        1  1.173290
31    -0.020285 -0.040362      27        1  1.170164
46    -0.113329  0.044465      28        1  1.168303
69    -0.045470  0.049602      29        1  1.097774
35    -0.101012  0.070984      30        1  1.094092
...         ...       ...     ...      ...       ...
6     -0.004990 -0.069005      71        1  0.458279
58    -0.039853 -0.039644      72        1  0.448090
16    -0.072813  0.072585      73        1  0.421815
5     -0.048434 -0.087153      74        1  0.419020
80     0.049047 -0.035825      75        1  0.403627
63     0.067067  0.043250      76        1  0.371010
72    -0.040330  0.089926      77        1  0.349209
59     0.008879  0.017129      78        1  0.332080
23     0.053658  0.040692      79        1  0.327353
83     0.010575 -0.091471      80        1  0.290892
14     0.053960 -0.090836      81        1  0.272278
2     -0.038430 -0.084069      82        1  0.271329
70    -0.047549  0.034671      83        1  0.245058
34    -0.041547 -0.096920      84        1  0.239906
26    -0.010261 -0.082055      85        1  0.237424
85    -0.039810 -0.057593      86        1  0.237285
28    -0.078501 -0.017909      87        1  0.219372
57    -0.008837 -0.115921      88        1  0.188386
97    -0.024318 -0.082975      89        1  0.177226
98     0.025269  0.016585      90        1  0.169738
81    -0.028516 -0.108919      91        1  0.125622
68    -0.013329 -0.116962      92        1  0.061507
64    -0.019488 -0.117321      93        1  0.059259
77    -0.013990 -0.125214      94        1  0.054857
42    -0.018322 -0.116561      95        1  0.048349
79    -0.017380 -0.112720      96        1  0.039479
73    -0.019754 -0.112278      97        1  0.035936
75    -0.020542 -0.107860      98        1  0.023697
48    -0.021090 -0.110711      99        1  0.015416
94    -0.020999 -0.108415     100        1  0.014056

[100 rows x 5 columns], topic_info=       Category         Freq          Term        Total  loglift  logprob
term                                                                     
356     Default  4705.000000          игра  4705.000000  30.0000  30.0000
517     Default  6573.000000             0  6573.000000  29.0000  29.0000
1075    Default  6537.000000          файл  6537.000000  28.0000  28.0000
1788    Default  5223.000000          сеть  5223.000000  27.0000  27.0000
1608    Default  5385.000000    устройство  5385.000000  26.0000  26.0000
59      Default  3314.000000        return  3314.000000  25.0000  25.0000
15

Можно посмотреть метрики.

In [11]:
import numpy as np

In [ ]:
coherence_model_lda = gensim.models.CoherenceModel(model=lda, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [ ]:
topics = []
for topic_id, topic in lda.show_topics(num_topics=100, formatted=False):
    topic = [word for word, _ in topic]
    topics.append(topic)

In [ ]:
coherence_model_lda = gensim.models.CoherenceModel(topics=topics, 
                                                   texts=texts, 
                                                   dictionary=dictinary, coherence='c_v')

In [ ]:
coherence_model_lda.get_coherence()

### 3) сделайте хороший словарь (отфильтруйте слишком частотные и редкие слова, попробуйте удалить стоп-слова)

- стоп-слова для английского и русского уже убрали
- нужно удалить странные штуки с lt;
- убрать одиночные буквы
- убрать цифры
- убрать все, что на латинице, потому что вылезают части кода

In [16]:
import string
import re

In [17]:
punct = string.punctuation

In [20]:
texts_cl_eng = texts

In [19]:
eng_str = 'QWERTYUIOPASDFGHJKLZXCVBNMqwertyuiopasdfghjklzxcvbnm'

In [21]:
stops_y = set(['алтухов', 'большой', 'бы', 'быть', 'в', 'весь', 'вот', 'все', 'всей', 'вы','г', 'говорить', 'год', 'да', 'для', 'до', 'еще', 'же', 'знать', 'и', 'из', 'к', 'как', 'который', 'мочь', 'мы', 'на', 'наш', 'не', 'него', 'нее', 'нет', 'них', 'но', 'о', 'один', 'она', 'они', 'оно', 'оный', 'от', 'ото', 'по', 'с', 'свой', 'себя', 'сказать', 'та', 'такой', 'только', 'тот', 'ты', 'у', 'что', 'это', 'этот', 'я'])

In [22]:
stops_new = set(['что', 'это', 'как', 'бесплтно', 'бесплатно', 'безкоштовно', 'даром', 'free', 'бесплтно', 'руками', 'самостоятельно', 'самодельный', 'скачать', 'download', 'драйвер', 'прошивка', 'порно', 'порнушка', 'вконтакте', 'доклад', 'porn', 'porno', 'sex', 'форум', 'реферат', 'статья', 'блог', 'хитрости', 'уловки', 'хабр', 'хабра', 'хабрхабр', 'faq', 'инструкция', 'википедия', 'вики', 'wikipedia', 'wiki', 'схема', 'состав', 'способ', 'методы', 'технология', 'торрент', 'торент', 'torrent', 'torent', 'torents', 'torrents', 'сонник', 'приснилось', 'прикол', 'смешно', 'юмор', 'анекдот', 'эротика', 'эротический', 'аамир', 'аариф', 'аарон', 'аасим', 'абан', 'аббас', 'абд', 'абдула', 'абдулла', 'абдульазиз', 'абдульазым', 'абдульали', 'абдульалим', 'абдульбари', 'абдульбасыт', 'абдульвадуд', 'абдульвахаб', 'абдульвахид', 'абдульгафар', 'абдульгафур', 'абдульджабар', 'абдульджалиль', 'абдулькадир', 'абдулькарим', 'абдулькахар', 'абдулькудус', 'абдульлатыф', 'абдульмаджид', 'абдульматин', 'абдульмуджиб', 'абдульмуиз', 'абдульмуталь', 'абдульмухаймин', 'абдульфатах', 'абдульхади', 'абдульхакам', 'абдульхаким', 'абдульхакк', 'абдульхалик', 'абдульхалим', 'абдульхамид', 'абдульхасиб', 'абдульхафиз', 'абдуннасер', 'абдурразак', 'абдуррауф', 'абдуррафи', 'абдуррахим', 'абдуррахман', 'абдуррашид', 'абдуссабур', 'абдуссалям', 'абдуссамад', 'абдуссами', 'абдутавваб', 'абдущщакур', 'абидин', 'або', 'абрам', 'абраха', 'абу', 'абульхайр', 'ава', 'авад', 'авангард', 'авва', 'аввакум', 'авгей', 'авгий', 'август', 'августин', 'авда', 'авдей', 'авделай', 'авдиес', 'авдий', 'авдикий', 'авдифакс', 'авдон', 'авенир', 'авентин', 'аверкий', 'аверьян', 'авив', 'авид', 'авим', 'авксентий', 'авкт', 'авраам', 'аврам', 'авраша', 'аврелий', 'аврор', 'авсей', 'автолик', 'автомедон', 'автоном', 'авудим', 'авундий', 'агав', 'агавва', 'агамемнон', 'аганя', 'агап', 'агапий', 'агапит', 'агапон', 'агафангел', 'агафодор', 'агафон', 'агафоник', 'агафоника', 'агафопод', 'агафопус', 'агаша', 'аггей', 'агей', 'агелай', 'агенор', 'агзам', 'аглаий', 'агн', 'агрий', 'адад', 'адам', 'адиб', 'аднан', 'адольф', 'адонис', 'адриан', 'адыль', 'аетий', 'азадан', 'азам', 'азамат', 'азар', 'азарий', 'азат', 'аззам', 'азиз', 'азий', 'азхар', 'аид', 'аифал', 'айдар', 'айет', 'айман', 'айнур', 'айрат', 'айтуган', 'айюб', 'акакий', 'акаша', 'акепсий', 'акепсим', 'акила', 'аким', 'акиндин', 'акинфий', 'акрам', 'аксен', 'акустий', 'акутион', 'алан', 'алар', 'алвиан', 'алевтин', 'алей', 'александр', 'алексей', 'алексий', 'ален', 'алет', 'алехандро', 'алеша', 'али', 'алим', 'алимпий', 'алипий', 'алканой', 'алкимедон', 'алкиной', 'алкмеон', 'аллар', 'алмас', 'алон', 'алфей', 'альаббас', 'альберт', 'альбин', 'альварес', 'альфонс', 'альфред', 'аляуддин', 'амадей', 'амвросий', 'амджад', 'амин', 'амир', 'аммар', 'аммон', 'аммун', 'амон', 'амонит', 'амос', 'амплий', 'амр', 'амфиан', 'амфилохий', 'амфион', 'ананда', 'ананий', 'анас', 'анастас', 'анастасий', 'анатолий', 'анатом', 'анвар', 'ангел', 'ангелар', 'ангий', 'андрей', 'андремон', 'андриан', 'андромаха', 'андрон', 'андроник', 'анект', 'анемподист', 'аний', 'аникита', 'анимаиса', 'анин', 'анис', 'анисим', 'анри', 'ансар', 'антей', 'антенор', 'антилох', 'антимах', 'антиной', 'антиох', 'антип', 'антипа', 'антипатр', 'антиф', 'антифат', 'антон', 'антоний', 'антонин', 'анту', 'антуан', 'ану', 'анубис', 'анувий', 'анурий', 'ануфрий', 'анфим', 'анфимий', 'анфипом', 'анфир', 'анфуса', 'анхиал', 'анхиз', 'апеллий', 'апизаон', 'апис', 'аполл', 'аполлинарий', 'аполлон', 'аполлоний', 'аполлос', 'апрониан', 'апфимедон', 'аргент', 'ардалион', 'арджуна', 'арей', 'аретос', 'арефа', 'арефий', 'ариадна', 'ариан', 'арий', 'арис', 'аристарх', 'аристид', 'аристион', 'аристовул', 'аристоклий', 'аркадий', 'аркисий', 'арнеон', 'арнольд', 'аронос', 'арпила', 'аррунс', 'арсен', 'арсений', 'арсентий', 'арслан', 'артамон', 'артем', 'артема', 'артемий', 'артемон', 'артур', 'аруру', 'архелий', 'архептолем', 'архип', 'архипп', 'арчил', 'арш', 'арэфа', 'асад', 'асадулла', 'асан', 'асинкрит', 'асиф', 'аскалаф', 'аскалон', 'асканий', 'асклепий', 'асклипиодот', 'аскольд', 'аслан', 'асма', 'ассарак', 'астафий', 'астерий', 'астий', 'астион', 'астионакс', 'астрид', 'ата', 'атаа', 'атеист', 'атон', 'атрей', 'аттий', 'аттик', 'атэ', 'аус', 'афанасий', 'афзал', 'афиноген', 'афинодор', 'афиф', 'афон', 'афоний', 'афоня', 'африкан', 'ахад', 'ахаз', 'ахаик', 'ахат', 'ахбар', 'ахила', 'ахилл', 'ахиллий', 'ахмад', 'ахмар', 'ахмат', 'ахунд', 'ацест', 'ашраф', 'аяз', 'аякс', 'баасым', 'бадруддин', 'бажен', 'бакир', 'балаш', 'бальтазар', 'барат', 'бартоломей', 'басам', 'басыль', 'батист', 'баха', 'бахауддин', 'бахир', 'бахиуддин', 'бахтияр', 'башаар', 'баяз', 'баян', 'бектуган', 'бел', 'белит сери', 'беллерофонт', 'бенедикт', 'берислав', 'бернард', 'бертольд', 'бертрам', 'бес', 'бианер', 'бидзин', 'бикбай', 'бикбулат', 'билал', 'билалль', 'битий', 'бишр', 'благомир', 'боб', 'богдан', 'боголеп', 'боеслав', 'болеслав', 'бонифатий', 'борей', 'боримир', 'борис', 'борислав', 'боян', 'бронислав', 'будимир', 'булат', 'буранбай', 'бурангул', 'буранша', 'бурхан', 'вавила', 'ваджих', 'вади', 'вадим', 'вазих', 'ваиль', 'вакил', 'вакх', 'валент', 'валентин', 'валера', 'валериан', 'валерий', 'вали', 'валид', 'валиуддин', 'вальтер', 'ваптос', 'варадат', 'варахий', 'варахисий', 'варвар', 'варипсав', 'варлаам', 'варлам', 'варнава', 'варсава', 'варсис', 'варсонофий', 'варул', 'варух', 'варфоломей', 'васил', 'василек', 'василид', 'василий', 'василиск', 'василько', 'васим', 'васой', 'васс', 'вассиан', 'вася', 'вафик', 'вафусий', 'вахид', 'вахрамей', 'вахтисий', 'вацлав', 'велимир', 'велислав', 'велор', 'вендимиан', 'венедикт', 'венедим', 'вениамин', 'вергилий', 'верк', 'вечеслав', 'вианор', 'викарий', 'викентий', 'виктор', 'викторин', 'вил', 'вилен', 'вилли', 'вильгельм', 'вильдан', 'вильям', 'винсент', 'вир', 'вирилад', 'виссарион', 'вит', 'виталий', 'витольд', 'витя', 'вифоний', 'влад', 'владилен', 'владимир', 'владислав', 'владлен', 'влас', 'власий', 'вова', 'воин', 'воислав', 'володар', 'волсцент', 'вольдемар', 'вольмир', 'вольф', 'вольфганг', 'воля', 'вонифатий', 'всеволод', 'всемил', 'вук', 'вукол', 'вулкан', 'вылко', 'вячеслав', 'габдулла', 'габит', 'габриель', 'гавведай', 'гавиний', 'гавриил', 'гаврила', 'гази', 'газиз', 'газим', 'гаий', 'гай', 'галактион', 'галиб', 'галик', 'галим', 'галионт', 'галиферс', 'гамалиил', 'гани', 'ганимед', 'гантиол', 'гапон', 'гарольд', 'гарри', 'гаррик', 'гасан', 'гастон', 'гата', 'гафар', 'гаян', 'гед', 'гектор', 'геласий', 'гелен', 'гелиан', 'гелий', 'геликаон', 'гелиос', 'гемелл', 'гена', 'геннадий', 'генрих', 'георгий', 'геракл', 'геральд', 'герасим', 'герберт', 'гервасий', 'геркулес', 'герман', 'германн', 'гермес', 'гермоген', 'геронтий', 'гертруд', 'гершель', 'гетион', 'гефест', 'гигантий', 'гильберт', 'гиппокоон', 'гипполох', 'гиппот', 'гиппофой', 'гипсенор', 'гиртак', 'гияс', 'главк', 'глеб', 'гликерий', 'гоброн', 'гор', 'горазд', 'горгий', 'горгоний', 'гордей', 'гордиан', 'гордий', 'горимир', 'горислав', 'горн', 'горус', 'гранит', 'грегор', 'григорий', 'гур', 'гурий', 'гурьян', 'густав', 'давид', 'давикт', 'давлет', 'давуд', 'давыд', 'дада', 'далмат', 'дамас', 'дамиан', 'дамир', 'дан', 'данай', 'данакт', 'даниил', 'данила', 'дар', 'дардан', 'дарес', 'дарий', 'дассий', 'дауд', 'даян', 'деифоб', 'декабрий', 'дементий', 'демид', 'демодок', 'демокоон', 'демократ', 'демосфен', 'демьян', 'дениз', 'денис', 'джабир', 'джавад', 'джалаль', 'джамаль', 'джамальуддин', 'джамиль', 'джафар', 'джек', 'джеральд', 'джим', 'джихад', 'джо', 'джозеф', 'джон', 'джордж', 'дидим', 'дидумос', 'дий', 'дик', 'дима', 'димант', 'димитриан', 'димитрий', 'диодор', 'диодот', 'диоклес', 'диомед', 'диомид', 'дион', 'дионисий', 'диоскор', 'дисан', 'дисидерий', 'дитрих', 'дияуддин', 'дмитрий', 'дмитро', 'добрыня', 'довмонт', 'долий', 'долион', 'долон', 'дометиан', 'дометий', 'домн', 'домнин', 'дональд', 'дональт', 'донат', 'доримедонт', 'дормидонт', 'дорофей', 'досифей', 'драгутин', 'дукитий', 'дула', 'евагрий', 'евангел', 'еварест', 'еввентий', 'еввул', 'евгений', 'евграф', 'евдоким', 'евдоксий', 'евелпист', 'евеопист', 'евиласий', 'евкарпий', 'евклий', 'евкул', 'евлампий', 'евлогий', 'евмений', 'евникиан', 'евноик', 'евод', 'евпл', 'евпор', 'евпсихий', 'евсевий', 'евсевон', 'евсей', 'евсигний', 'евстафий', 'евстахий', 'евстигней', 'евстохий', 'евстратий', 'евсхимон', 'евтихиан', 'евтихий', 'евтропий', 'евфимиан', 'евфимий', 'евфрасий', 'евфросин', 'егор', 'едесий', 'екдит', 'ексакустодиан', 'елеазар', 'елевсипп', 'елевферий', 'елезвой', 'елизар', 'елизбар', 'елисей', 'елистрат', 'елладий', 'еллий', 'елпидий', 'елпидифор', 'емелиан', 'емельян', 'емеля', 'емилиан', 'енелпист', 'епафрас', 'епафродит', 'епенет', 'епикнет', 'епиктет', 'епимах', 'епифан', 'епифаний', 'епполоний', 'еразм', 'ераст', 'ерема', 'еремей', 'ерм', 'ермак', 'ермий', 'ермил', 'ерминингельд', 'ермипп', 'ермоген', 'ермократ', 'ермолай', 'ерос', 'ерофей', 'еруслан', 'еспер', 'еферий', 'ефив', 'ефим', 'ефимий', 'ефрем', 'жак', 'жан', 'ждан', 'жозеф', 'жорж', 'жюль', 'жюльен', 'зайд', 'закарийя', 'закария', 'заки', 'закир', 'закхей', 'замам', 'зафир', 'захар', 'захария', 'захид', 'захир', 'зевин', 'зевс', 'зенон', 'зефир', 'зигмунд', 'зигфрид', 'зиннур', 'зиновий', 'зинон', 'зияд', 'зоил', 'зорий', 'зосим', 'зосима', 'зот', 'зотик', 'зульфикар', 'зухайр', 'иадор', 'иакинф', 'иакисхол', 'иаков', 'иамвлих', 'ианикит', 'ианнуарий', 'иасон', 'ибрагим', 'ибрахим', 'иван', 'игафракс', 'игнатий', 'игорь', 'идей', 'идоменей', 'идрис', 'иезекииль', 'иеракс', 'иеремия', 'иерон', 'иероним', 'иерофей', 'из', 'иззуддин', 'измаил', 'изяслав', 'иисус', 'ий', 'икар', 'икарий', 'икрам', 'ил', 'иларий', 'иларион', 'илиан', 'илиодор', 'илионей', 'илларион', 'иллирик', 'ильгиз', 'ильдар', 'ильдус', 'ильшат', 'илья', 'имад', 'имадуддин', 'иман', 'имил', 'иммануил', 'имран', 'имхатеп', 'инвикт', 'индис', 'иней', 'иннокентий', 'инсар', 'инсаф', 'иоад', 'иоаким', 'иоанн', 'иоанникий', 'иоасаф', 'иов', 'иоганн', 'иоиль', 'иосиф', 'ипат',
             'ипатий', 'иперехий', 'ипполит', 'иракламвон', 'ираклемон', 'ираклий', 'ирек', 'иринарх', 'ириней', 'ириний', 'ирнини', 'иродион', 'ирфан', 'иса', 'исаак', 'исаакий', 'исавр', 'исаия', 'исай', 'исак', 'исам', 'исе', 'исидор', 'исихий', 'искандер', 'иской', 'ислам', 'исмагил', 'исмаил', 'исмат', 'истукарий', 'исфандияр', 'исхак', 'иттифак', 'иувеналий', 'иувентин', 'иувиналий', 'иуда', 'иулиан', 'иулий', 'иуст', 'иустин', 'иустиниан', 'ифидамас', 'ификл', 'ифит', 'ихи', 'ихсан', 'ишбулат', 'ишбулды', 'ишгильды', 'иштуган', 'ишуллану', 'июлий', 'кабир', 'кадм', 'кадыр', 'казимир', 'кайс', 'каленик', 'калигула', 'калиник', 'калистрат', 'каллимах', 'каллиник', 'каллиопий', 'каллист', 'каллистрат', 'калуф', 'калхас', 'камал', 'камиль', 'кандид', 'каниз', 'кантидиан', 'кантидий', 'капаней', 'капик', 'капис', 'капитон', 'карим', 'карион', 'карл', 'карп', 'картерий', 'касим', 'кассиан', 'кастор', 'кастрикий', 'кастул', 'касым', 'касьян', 'катерий', 'катилл', 'катун', 'кашфулла', 'каюм', 'квинтилиан', 'кебрен', 'кебрион', 'келестин', 'келсий', 'кенсорин', 'кесарий', 'кесарь', 'кетевань', 'кеша', 'кикн', 'ким', 'киндей', 'кион', 'киприан', 'кир', 'кириак', 'кириан', 'кирик', 'кирилл', 'кирин', 'кирион', 'кирсан', 'кирьян', 'клавдиан', 'клавдий', 'клавз', 'клемент', 'клеоник', 'клим', 'климент', 'климентий', 'клитий', 'кодрат', 'коинт', 'колумбий', 'конан', 'кондрат', 'кондратий', 'конкордий', 'конон', 'конрад', 'константин', 'констанций', 'консуэло', 'коон', 'коприй', 'корас', 'кореб', 'корней', 'корнелий', 'корнил', 'корнилий', 'корнут', 'корон', 'коронат', 'косма', 'краснослав', 'крискент', 'крискентиан', 'крисп', 'кристиан', 'кристоф', 'кронид', 'кронион', 'ксантиппа', 'ксанфий', 'ксанфиппа', 'ксенофонт', 'ктезипп', 'ктесей', 'куарт', 'кудама', 'кузьма', 'кукша', 'куприян', 'курбан', 'курбат', 'кутайба', 'кутоний', 'куфий', 'лабиб', 'лавз', 'лавр', 'лаврентий', 'лазарь', 'лампад', 'ланселот', 'лаодам', 'лаодикий', 'лаодок', 'лаокоон', 'лаомедонт', 'ларгий', 'ларион', 'лариса', 'латин', 'лаэрт', 'леандр', 'лев', 'левк', 'левкий', 'лель', 'лениан', 'леня', 'леодей', 'леон', 'леонард', 'леонид', 'леонт', 'леонтей', 'леонтий', 'либерии', 'либерт', 'ливерий', 'ливий', 'ликаон', 'ликарион', 'ликомед', 'лимний', 'лин', 'лир', 'лисимах', 'лолий', 'лонгин', 'лот', 'луарсаб', 'луи', 'лука', 'лукиан', 'лукий', 'лукиллиан', 'лукман', 'лукьян', 'лупп', 'люаи', 'любим', 'любомир', 'любослав', 'людвиг', 'люксен', 'лютфи', 'маазин', 'маахир', 'мавр', 'маврикий', 'мавсима', 'магафур', 'магистриан', 'магн', 'магсум', 'маджит', 'мадлен', 'мажд', 'мажди', 'маждуддин', 'майрам', 'майсара', 'майслав', 'майсур', 'макар', 'макарий', 'македоний', 'макин', 'макровий', 'макс', 'максиан', 'максим', 'максимиан', 'максимилиан', 'максимиллиан', 'максимильян', 'максуд', 'максуз', 'малик', 'малх', 'мамант', 'мамдух', 'маммий', 'мамнун', 'мансур', 'мануил', 'манфред', 'мар', 'марван', 'мардарий', 'мардоний', 'марзук', 'мари', 'мариав', 'мариамна', 'марий', 'марин', 'марк', 'маркелл', 'маркеллин', 'маркиан', 'марлен', 'марон', 'марсалий', 'марсен', 'мартиан', 'мартин', 'мартиниан', 'мартирий', 'мартын', 'маруф', 'маснави', 'масуд', 'матвей', 'матфей', 'матфий', 'махаон', 'махди', 'махмуд', 'мегапенф', 'мегей', 'медимн', 'медон', 'мезенций', 'мелампод', 'мелантий', 'меласипп', 'мелевсипп', 'мелентий', 'мелетий', 'мелиссен', 'мелитон', 'мемнон', 'менандр', 'менелай', 'менесфей', 'менетий', 'менигн', 'ментес', 'ментор', 'мерген', 'мерион', 'меркурий', 'мертий', 'мессап', 'метиск', 'метопт', 'мефодий', 'мечислав', 'миан', 'мигдоний', 'мигшдон', 'мидхад', 'милад', 'милан', 'милен', 'милий', 'милонег', 'милослав', 'милютин', 'мин', 'миней', 'минеон', 'минос', 'минсифей', 'мир', 'миракс', 'мирон', 'мирослав', 'миртил', 'мисаил', 'мисбах', 'митра', 'митридат', 'митрофан', 'митя', 'мифтах', 'михаил', 'михей', 'мичура', 'модест', 'моисей', 'мокий', 'молосс', 'морон', 'мстислав', 'муаз', 'муайид', 'мувафак', 'муддарис', 'муджахид', 'муккарам', 'муко', 'мунзир', 'мунир', 'мунис', 'мунтасир', 'мурат', 'муртади', 'муса', 'муслим', 'мустафа', 'мут', 'мутаа', 'мутазз', 'мутасим', 'мути', 'муфид', 'мухаммад', 'мухаммед', 'муханнад', 'мухсин', 'мухтади', 'мухтар', 'наасим', 'наби', 'набиль', 'набих', 'набу', 'набхан', 'навплий', 'наджи', 'наджиб', 'наджмуддин', 'надим', 'надир', 'назар', 'назарий', 'назим', 'назир', 'назих', 'наиль', 'наим', 'намтар', 'нариман', 'наркис', 'наркисс', 'насим', 'насих', 'насреддин', 'нассеруддин', 'натан', 'наум', 'нафанаил', 'неделя', 'нейтх', 'нектарий', 'нелей', 'неон', 'неонил', 'неоптолем', 'неофит', 'нергал', 'нерей', 'нестор', 'нефмон', 'нефтис', 'низ', 'низам', 'никандр', 'никанор', 'никита', 'никифор', 'никодим', 'никола', 'николай', 'никон', 'никострат', 'никтополион', 'нил', 'ниниб', 'нисон', 'нит', 'нифонт', 'новомир', 'ной', 'норберт', 'норд', 'норман', 'нот', 'нуман', 'нуруддин', 'нух', 'овидий', 'одиссей', 'оилей', 'океан', 'октавиан', 'октябрин', 'октябрь', 'олаф', 'олег', 'олжас', 'оливер', 'олимп', 'олимпан', 'олимпий', 'ольгерд', 'омар', 'омврий', 'омейр', 'омран', 'оней', 'онисий', 'онисим', 'онисифор', 'оноре', 'онуфрий', 'опис', 'ор', 'орентий', 'орест', 'орион', 'орифаон', 'ормен', 'орменон', 'оронт', 'орфей', 'освальд', 'осип', 'осирис', 'оскар', 'остап', 'острихий', 'остромир', 'от', 'отто', 'оферионей', 'охрид', 'павлик', 'павлин', 'павсикакий', 'павсилип', 'паисий', 'паламед', 'палиас', 'палий', 'палладий', 'паллант', 'памва', 'памвон', 'памфалон', 'памфамир', 'памфил', 'пандар', 'панкратий', 'панлихарий', 'пансофий', 'пантелеймон', 'панфил', 'панфой', 'папа', 'папий', 'папила', 'парамон', 'пард', 'паригорий', 'парис', 'пармен', 'пармений', 'парод', 'партизан', 'парфений', 'пасикрат', 'патапий', 'патермуфий', 'патрикей', 'патрикий', 'патров', 'патрокл', 'пафнутий', 'пахом', 'пахомий', 'пелей', 'пелий', 'пелопс', 'пеон', 'перегрин', 'пересвет', 'перифас', 'перифой', 'персей', 'петей', 'петр', 'пигасий', 'пизаидр', 'пизандр', 'пизистрат', 'пий', 'пилад', 'пилон', 'пимен', 'пинна', 'пионий', 'пирей', 'пирехм', 'пирр', 'пист', 'питирим', 'платон', 'плисфен', 'плутон', 'подарк', 'пой', 'полиб', 'полидам', 'полидевк', 'полидор', 'полиевкт', 'полиен', 'поликарп', 'полиместор', 'полиник', 'полинур', 'полипетю', 'полит', 'полифем', 'полихроний', 'полувий', 'помпеи', 'помпей', 'помпий', 'понтий', 'поплии', 'поплий', 'порфирий', 'посейдон', 'потамий', 'потап', 'потит', 'приам', 'прилидиан', 'принкипс', 'приск', 'провий', 'прозор', 'прокесс', 'прокл', 'прокоп', 'прокопий', 'прокофий', 'прокул', 'протас', 'протасий', 'протезилай', 'протей', 'протерий', 'протоген', 'протолеон', 'профан', 'прохор', 'псой', 'птах', 'пуд', 'пузур бел', 'пуплий', 'ра', 'рабах', 'раби', 'равиль', 'рагиб', 'раджаб', 'радий', 'радим', 'радимир', 'радислав', 'радомир', 'радослав', 'ражден', 'разумник', 'раид', 'ракин', 'рамаз', 'рамиз', 'рамиль', 'расиль', 'расим', 'расих', 'рассул', 'ратиб', 'ратибор', 'ратмир', 'рауф', 'рафаил', 'рафи', 'рафик', 'рахим', 'рахман', 'рашад', 'рашид', 'реас', 'ревмир', 'ревокат', 'рез', 'рексенор', 'рем', 'ренат', 'ридван', 'ризван', 'рикс', 'ричард', 'рияд', 'роберт', 'родерик', 'родион', 'родопиан', 'ролан', 'роланд', 'роман', 'ромил', 'ромул', 'ростислав', 'рубен', 'рудольф', 'руслан', 'рустам', 'рустик', 'руф', 'руфин', 'рушан', 'рэм', 'рюрик', 'саад', 'сабир', 'сабит', 'сабих', 'савва', 'савватий', 'савел', 'савелий', 'саверий', 'савин', 'саджид', 'садок', 'садоф', 'садри', 'садык', 'сазон', 'саид', 'сайид', 'сайфи', 'сайфуддин', 'сакердон', 'сакиб', 'салават', 'саламан', 'салах', 'салахуддин', 'салем', 'салим', 'салих', 'салман', 'салмоней', 'сальвадор', 'самад', 'самеи', 'самиир', 'самир', 'самон', 'сампсон', 'самсон', 'самуил', 'саня', 'сарвил', 'сарпедон', 'сасоний', 'сатир', 'саторин', 'саторний', 'саторнил', 'саторнин', 'саттар', 'сатурн', 'сатурнин', 'саул', 'сафван', 'сафи', 'сахир', 'саша', 'свет', 'светлан', 'светозар', 'светослав', 'святогор', 'святополк', 'святослав', 'севастиан', 'севастьян', 'север', 'севериан', 'северин', 'северьян', 'севир', 'секунд', 'селевк', 'селевкий', 'селиний', 'селькис', 'семен', 'сеннис', 'сеня', 'серапион', 'серапис', 'серафим', 'сергей', 'сергий', 'сет', 'сивел', 'сигиц', 'сидор', 'сизиф', 'сикст', 'сила', 'силан', 'силантий', 'силуан', 'сильван', 'сильвест', 'сильвестр', 'симбир', 'симеон', 'симоисий', 'симон', 'симфориан', 'син', 'синон', 'сионий', 'сирадж', 'сисиний', 'сисой', 'слава', 'славомир', 'смарагд', 'собек', 'совет', 'созонт', 'сок', 'сократ', 'соломон', 'солохон', 'сонирил', 'сосий', 'сосипатр', 'сосс', 'соссий', 'сосфен', 'софрон', 'софроний', 'спартак', 'спевсипп', 'сперхий', 'спиридон', 'сталь', 'станислав', 'стахий', 'стентор', 'степан', 'стефан', 'стратион', 'стратон', 'стратоник', 'стратор', 'строфий', 'студий', 'субхи', 'суимвл', 'сулейман', 'султан', 'суляйман', 'сумукан', 'сууд', 'сухайб', 'сухайль', 'сухий', 'сфенел', 'сысой', 'таамир', 'таахир', 'таврион', 'тагир', 'таир', 'таймулла', 'тайсир', 'талаль', 'таламон', 'талха', 'тальфибий', 'тамам', 'таммуз', 'тансылу', 'тантал', 'тарас', 'тарасий', 'тарах', 'тарик', 'тариф', 'таричан', 'тарфах', 'татион', 'тауфик', 'тахир', 'тевер', 'тевкр', 'тезей', 'теймураз', 'телем', 'телемах', 'телеф', 'теодор', 'терентий', 'тертий', 'тивуртий', 'тигран', 'тигрий', 'тидей', 'тимолай', 'тимон', 'тимофей', 'тимур', 'тиндарей', 'тиррей', 'тирсей', 'тит', 'титий', 'тифон', 'тихик', 'тихомир', 'тихон', 'тлеполем', 'толя', 'том', 'томас', 'тоос', 'тот', 'тоша', 'транквиллин', 'трерис', 'трибун', 'тривимий', 'тристан', 'тритон', 'трифиллий', 'трифон', 'троадий', 'троил', 'трой', 'трофим', 'турвон', 'турн', 'туссэн', 'уалент', 'уалентин', 'уалерий', 'уалириан', 'уар', 'убада', 'убай', 'убайда', 'убара туму', 'уврикий', 'узбек', 'укба', 'ульмас', 'ульрих', 'умайр', 'умар', 'упуаут', 'ур эа', 'урал', 'урван', 'уриил', 'урош', 'урпасиан', 'урус', 'усама', 'усман', 'устин', 'ут напиштим', 'утба', 'фавий', 'фавмасий', 'фавн', 'фавст', 'фавстиан', 'фавуаз', 'фаддей', 'фадей', 'фади', 'фадль', 'фадлюллах', 'фаиз', 
    'фаик', 'файзулла', 'файсал', 'фал', 'фалалей', 'фалассий', 'фаллелей', 'фанис', 'фантин', 'фарид', 'фарис', 'фармуфий', 'фарнакий', 'фарук', 'фархад', 'фатин', 'фатих', 'фауст', 'фахад', 'фахир', 'фахри', 'фаяз', 'феб', 'февралин', 'фегей', 'федим', 'федон', 'федор', 'федос', 'федосей', 'федосий', 'федот', 'федотий', 'федул', 'феклист', 'феликс', 'фемий', 'фемистокл', 'фемистоклей', 'феникс', 'фенникс', 'феоген', 'феогнид', 'феогний', 'феогност', 'феодор', 'феодорит', 'феодосий', 'феодот', 'феодох', 'феодул', 'феоклимен', 'феоктирист', 'феоктист', 'феопемпт', 'феопист', 'феопрепий', 'феост', 'феостирикт', 'феостих', 'феотекн', 'феотих', 'феофан', 'феофил', 'феофилакт', 'ферапонт', 'фердинанд', 'ферм', 'ферсандр', 'ферсит', 'феспесий', 'феспорт', 'фидель', 'филагрий', 'филадельф', 'филарет', 'филат', 'филей', 'филетер', 'филикиссим', 'филикс', 'филимон', 'филипп', 'филит', 'филл', 'филогоний', 'филоктeт', 'филоктимон', 'филолог', 'филон', 'философ', 'филотий', 'филофей', 'филумен', 'фимэт', 'финеес', 'финей', 'фирмин', 'фирмос', 'фирс', 'фифаил', 'флавиан', 'флавий', 'флегонт', 'флор', 'флорентий', 'флоренц', 'флорин', 'фоас', 'фока', 'фома', 'фоон', 'форвин', 'фортунат', 'фостирий', 'фот', 'фотий', 'фотин', 'франк', 'франц', 'франциск', 'фрасимед', 'фридрих', 'фрол', 'фроний', 'фронтасий', 'фронтис', 'фрументий', 'фуад', 'фулвиан', 'фусик', 'хаашим', 'хабиб', 'хабибулла', 'хади', 'хадис', 'хаим', 'хайдар', 'хайри', 'хайруддин', 'хайсам', 'хаким', 'халдун', 'халид', 'халил', 'халилль', 'хамза', 'хамид', 'хани', 'харалампий', 'харис', 'харисим', 'харитон', 'харлампий', 'харон', 'харун', 'хасан', 'хассан', 'хатим', 'хатор', 'хафиз', 'хашим', 'херимон', 'хикмет', 'хирон', 'хнум', 'ходжа', 'хонс', 'храбр', 'хрис', 'хрисанта', 'хрисанф', 'хрисипп', 'хрисогон', 'хрисотель', 'христиан', 'христофор', 'худ', 'худион', 'хузайма', 'хузайфа', 'хумам', 'хумбаба', 'хусам', 'хусамуддин', 'хусдазат', 'хуссейн', 'цезарь', 'цекул', 'цетон', 'часлав', 'чеслав', 'чингиз', 'шади', 'шакир', 'шалва', 'шамаш', 'шамиль', 'шамси', 'шариф', 'шафик', 'шахрияр', 'шепре', 'шерлок', 'шимшон', 'шио', 'шихаб', 'шура', 'эа', 'эварндр', 'эвдор', 'эвемон', 'эвмед', 'эвмел', 'эвриал', 'эврибат', 'эвридам', 'эврилох', 'эвримах', 'эврином', 'эврипил', 'эврисак', 'эврисфей', 'эврит', 'эвфорб', 'эгипс', 'эгиптий', 'эгисф', 'эгмонт', 'эдвард', 'эдик', 'эдип', 'эдит', 'эдуард', 'электрон', 'элизбар', 'элой', 'элопей', 'эльбрус', 'эльдар', 'эльпепор', 'эмели', 'эмилий', 'эмиль', 'эммануил', 'энгель', 'эней', 'энергий', 'эниопей', 'эномай', 'эол', 'эос', 'эпей', 'эпикл', 'эразм', 'эраст', 'эрик', 'эрихтопий', 'эрнест', 'эрнст', 'эрот', 'эсфирь', 'этеоней', 'эфиальт', 'эфопс', 'эфра', 'эхеней', 'эхепел', 'эхет', 'эхефрон', 'ювеналий', 'ювентин', 'ювиналий', 'юджин', 'юлдаш', 'юлиан', 'юлий', 'юнус', 'юпитер', 'юра', 'юрий', 'юст', 'юстин', 'юстиниан', 'юсуф', 'ютурна', 'юхан', 'ядгар', 'яков', 'якуб', 'якут', 'ямал', 'яман', 'ян', 'яннуарий', 'януарий', 'янус', 'яромир', 'ярополк', 'ярослав', 'ясар', 'ясий', 'ясин', 'ясон', 'яхья', 'аалия', 'аамаль', 'аасма', 'абир', 'аблаа', 'августа', 'авгэ', 'авдотья', 'аврелия', 'аврора', 'агапия', 'агата', 'агафия', 'агафоклия', 'агафья', 'аглаида', 'аглая', 'агнеса', 'агнесса', 'агния', 'аграфена', 'агриппина', 'ада', 'адаб', 'аделаида', 'аделина', 'аделия', 'адель', 'адиля', 'адриана', 'аеропа', 'аза', 'азалия', 'азария', 'азза', 'азиза', 'аида', 'айгуль', 'айда', 'айех', 'айша', 'айя', 'акилина', 'аксинья', 'акулина', 'алевтина', 'александра', 'алена', 'алина', 'алиса', 'алия', 'алкибия', 'алкимена', 'алкмена', 'алла', 'аллекто', 'алона', 'альба', 'альберта', 'альбертина', 'альбина', 'алькандра', 'альма', 'альмас', 'альфира', 'аля', 'амалия', 'амаль', 'амани', 'амата', 'аматулла', 'амели', 'амина', 'амира', 'амна', 'амфирея', 'амфитрита', 'анан', 'анания', 'анастасия', 'анатолия', 'анбар', 'ангелина', 'анета', 'анжела', 'анжелика', 'аниса', 'анисия', 'анисья', 'анита', 'анна', 'антиклея', 'антиопа', 'антонида', 'антонина', 'антония', 'антуанетта', 'анфиса', 'анфия', 'аполлинария', 'апраксия', 'апфия', 'арабелла', 'арва', 'арета', 'арибах', 'аридж', 'арина', 'аркадия', 'арсения', 'артемида', 'артемия', 'аруб', 'архелая', 'асалах', 'асах', 'асилях', 'асия', 'аскитри', 'аскитрия', 'асклиада', 'асклипиодота', 'аслия', 'аспазия', 'астинома', 'астиоха', 'астра', 'ася', 'атемия', 'афанасия', 'афаф', 'афина', 'афраа', 'афрах', 'афродита', 'ахд', 'ахия', 'ахлям', 'аэлита', 'аэлла', 'баасыма', 'бадрийя', 'бажена', 'балкис', 'банан', 'бану', 'басма', 'бастет', 'басыма', 'батуль', 'батэйя', 'бахийя', 'башиира', 'башира', 'беата', 'беатриса', 'бела', 'белла', 'берислава', 'берта', 'бика', 'бланка', 'бланш', 'богдана', 'божана', 'болеслава', 'борислава', 'боряна', 'бояна', 'бранислава', 'бремуза', 'брисеида', 'бронислава', 'бусайна', 'бушра', 'валентина', 'валериана', 'валерия', 'валиулла', 'валия', 'валя', 'ванда', 'варвара', 'василина', 'василиса', 'василисса', 'васса', 'вата', 'вафа', 'вацлава', 'вевея', 'вега', 'веда', 'вела', 'велислава', 'венера', 'вениамина', 'вера', 'вероника', 'веселина', 'веста', 'вивиан', 'видана', 'викторина', 'виктория', 'вилена', 'виола', 'виргиния', 'виринея', 'вита', 'виталина', 'виталия', 'влада', 'владилена', 'владимира', 'владислава', 'владлена', 'власта', 'всеслава', 'гаафа', 'габриэлла', 'гада', 'гаиания', 'гайда', 'гайша', 'гайя', 'галатея', 'гали', 'галима', 'галина', 'галия', 'галя', 'ганна', 'гасун', 'гаяна', 'геба', 'гезиона', 'гекамеда', 'гекуба', 'гелена', 'гелия', 'гелла', 'генриетта', 'гера', 'герда', 'гермиона', 'гертруда', 'гизела', 'гипподамия', 'гипполита', 'гира', 'глафира', 'гликерия', 'глория', 'голиндуха', 'голуба', 'горислава', 'грация', 'груня', 'груша', 'гуль', 'гульзар', 'гульнара', 'дайна', 'дана', 'дания', 'дарена', 'дарина', 'дария', 'дарья', 'дарьяна', 'дафния', 'дебора', 'дейзи', 'декабрина', 'делия', 'дельфина', 'деримахия', 'дериона', 'дея', 'джаля', 'джамиля', 'джанан', 'джемила', 'джемма', 'джина', 'джоконда', 'джульетта', 'джумана', 'диана', 'дидамия', 'дидона', 'дилара', 'дильбара', 'дина', 'динара', 'диодора', 'дионисия', 'добрава', 'долорес', 'доминика', 'домна', 'домника', 'домнина', 'дора', 'доротея', 'дорофея', 'драгомира', 'дросида', 'дуклида', 'духа', 'ева', 'еванфия', 'еввула', 'евгения', 'евдокия', 'евдоксия', 'евлалия', 'евлампия', 'евникия', 'евпейф', 'евпраксия', 'евсевия', 'евстолия', 'евтихия', 'евтропия', 'евфалия', 'евфимия', 'евфрасия', 'евфросиния', 'евфросинья', 'екатерина', 'елена', 'елизавета', 'еликонида', 'елима', 'елисавета', 'еннава', 'епистимия', 'епихария', 'ермиония', 'еротиида', 'есения', 'есфирь', 'ефимия', 'ефросиния', 'ефросинья', 'жанна', 'ждана', 'женевьева', 'жизель', 'жозефина', 'жюльетта', 'забира', 'заира', 'зайна', 'зайнаб', 'зайнулла', 'зайтуна', 'закийя', 'закия', 'замира', 'замфира', 'зара', 'зарина', 'зафира', 'захира', 'захра', 'захрах', 'звенислава', 'зиля', 'зина', 'зинаида', 'зиннат', 'зиновия', 'зита', 'зифа', 'зия', 'злата', 'зоиса', 'зоя', 'зульфия', 'зухра', 'ибтихадж', 'иванна', 'иветта', 'ида', 'идея', 'идофея', 'изабелла', 'издихар', 'изида', 'изис', 'изольда', 'изот', 'икрима', 'илария', 'илия', 'ильхам', 'имтисаль', 'инайя', 'инам', 'инас', 'инга', 'индира', 'инес', 'инесса', 'инна', 'интисар', 'иоанна', 'иовилла', 'иоланта', 'иона', 'иосия', 'ипатия', 'ипполита', 'ираида', 'ираклия', 'ирида', 'ирина', 'ироида', 'исидора', 'искра', 'иулиания', 'иулита', 'иулия', 'иуния', 'иустина', 'ифигения', 'ифимедея', 'ифиноя', 'ифиона', 'иштар', 'ия', 'каздоя', 'казимира', 'кайета', 'калерия', 'каликэ', 'калина', 'калипсо', 'калиса', 'калисса', 'калисфения', 'каллиста', 'камелия', 'камилла', 'камиля', 'камля', 'капитолина', 'карима', 'карина', 'кармен', 'каролина', 'касима', 'касиния', 'кассандра', 'катада', 'катерина', 'катиба', 'катя', 'керкира', 'кибела', 'кикилия', 'килисса', 'киматоя', 'киприда', 'кира', 'кириакия', 'кириена', 'кирилла', 'кифа', 'клавдия', 'клара', 'клариса', 'клеопа', 'клеопатра', 'климена', 'климентина', 'клитемнестра', 'клония', 'коломбина', 'конкордия', 'констанция', 'кора', 'корделия', 'крискентия', 'кристина', 'ксана', 'ксения', 'кульсум', 'кяукаб', 'кяусар', 'лавиния', 'лада', 'лайла', 'лала', 'лампеция', 'лаодамия', 'лаодика', 'латона', 'латыфа', 'лаура', 'левкофея', 'леда', 'лейла', 'лена', 'лениана', 'ленина', 'леонида', 'леонила', 'леонора', 'леонтия', 'лера', 'леся', 'ливия', 'лидия', 'лилиана', 'лилия', 'лина', 'линда', 'лия', 'лола', 'лолита', 'лора', 'луиза', 'лукерия', 'лукерья', 'лукиана', 'лукина', 'лукия', 'лукреция', 'лутфулла', 'любаба', 'любава', 'любовь', 'любомира', 'людвига', 'людмила', 'люси', 'люция', 'ляма', 'лямис', 'лямья', 'маат', 'мавийя', 'мавлюда', 'мавра', 'магда', 'магдалина', 'маджида', 'маджиида', 'мадина', 'мадиха', 'май', 'маййяда', 'маймуна', 'майса', 'майсун', 'майя', 'макарим', 'макрина', 'маланто', 'маланья', 'малахия', 'малика', 'мальвина', 'маляк', 'мамелхва', 'мамету', 'мамика', 'маналь', 'манар', 'манефа', 'марам', 'маргарита', 'мариана', 'марианна', 'марина', 'марионилла', 'мария', 'марлена', 'марта', 'марфа', 'марьям', 'мастридия', 'матильда', 'матрена', 'матрона', 'маха', 'маша', 'мая', 'мегара', 'медея', 'мелания', 'мелисса', 'мелитина', 'мерседес', 'милада', 'милана', 'милица', 'милослава', 'миляуша', 'мина', 'минерва', 'минодора', 'мира', 'мирабелла', 'миранда', 'миропия', 'мирослава', 'мирра', 'митродора', 'млада', 'моико', 'моника', 'мстислава', 'муавийя', 'муза', 'муна', 'мунира', 'муфида', 'мухджа', 'мушира', 'набиля', 'набиха', 'навсикая', 'нада', 'надва', 'надежда', 'наджат', 'наджах', 'наджва', 'наджиба', 'наджия', 'наджйя', 'наджля', 'надида', 'надира', 'надия', 'надья', 'назаха', 'назийя', 'назира', 'назиха', 'наиля', 'наима', 'наина', 'найля', 'нана', 'насира', 'настасья', 'настя', 'насыха', 'наталия', 'наталья', 'науваль', 'наувар', 'науфаль', 'нафиса', 'нахля', 'нашида', 'нашита', 'некиппа', 'нелли', 'неонила', 'неонилла', 'нерина', 'несаим', 'неэра', 'нибааль', 'нида', 'ника', 'никиппа', 'нимаат', 'нимфодора', 'нина', 'ниназу', 
    'нинелла', 'нинель', 'нинон', 'нинсуи', 'ниоба', 'нирса', 'новелла', 'нонна', 'нора', 'нузар', 'нузха', 'нунехия', 'нур', 'нури', 'нурулла', 'нусайба', 'нут', 'нуф', 'нуха', 'ойгуль', 'оксана', 'октавия', 'октябрина', 'олеся', 'оливия', 'олимпиада', 'олимпия', 'ольга', 'оля', 'осия', 'офелия', 'павла', 'павлина', 'паллада', 'палома', 'пальмира', 'памела', 'пандора', 'параскева', 'патриция', 'паула', 'пелагея', 'пелагия', 'пенелопа', 'пенфесилия', 'перпетуя', 'персефона', 'петрония', 'пиама', 'пинна', 'платонида', 'полактия', 'полетта', 'полидамна', 'поликсена', 'поликсения', 'полина', 'поплия', 'правдина', 'прасковья', 'препедигна', 'преслава', 'прискилла', 'проскудия', 'пульхерия', 'рабаб', 'рабиа', 'рабига', 'равийя', 'равула', 'рагд', 'рада', 'раджа', 'радмила', 'радуа', 'радыйя', 'раида', 'раиса', 'раймонда', 'райя', 'ракия', 'рана', 'ранд', 'ранийя', 'рауда', 'рафа', 'рахиль', 'раша', 'рашида', 'ревекка', 'ревмира', 'регина', 'рената', 'рея', 'рида', 'риза', 'рим', 'рима', 'римма', 'рипсимия', 'рита', 'рогенда', 'рогнеда', 'роза', 'розалия', 'розана', 'розмари', 'роксана', 'роланда', 'ростислава', 'рувайда', 'рукайя', 'рукан', 'русана', 'руслана', 'руфина', 'руфь', 'саалима', 'сабина', 'сабира', 'савда', 'савсан', 'сайфулла', 'сакина', 'салима', 'салиха', 'саломея', 'сальва', 'сальма', 'самаах', 'самар', 'самийя', 'самира', 'самиха', 'самойла', 'сана', 'санаа', 'сания', 'сара', 'сараа', 'сарийя', 'сарра', 'сафа', 'сафия', 'сахар', 'сахля', 'света', 'светлана', 'светлозара', 'светозара', 'светослава', 'свобода', 'святослава', 'севастиана', 'севастьяна', 'северина', 'селена', 'селестина', 'сельвия', 'сельма', 'семирамида', 'серафима', 'сехмет', 'сешат', 'сибиллы', 'сивилла', 'сидури', 'силили', 'сильва', 'симона', 'синклитикия', 'сира', 'сихам', 'славяна', 'смарагда', 'снандулия', 'снежана', 'соломея', 'соломония', 'сосанна', 'сосипатра', 'софия', 'софония', 'софья', 'станимира', 'станислава', 'стелла', 'степанида', 'стефанида', 'стефания', 'сумайя', 'сурайя', 'сусанна', 'суха', 'сухайля', 'сухайма', 'сухайр', 'сюзанна', 'тавифа', 'таира', 'таисия', 'талия', 'тамазур', 'тамара', 'тара', 'таруб', 'татиана', 'татьяна', 'тахира', 'текла', 'текмесса', 'тереза', 'тина', 'тиро', 'тома', 'трифена', 'трояна', 'уаджиха', 'уалентина', 'уарда', 'уафа', 'уафика', 'уафия', 'уидад', 'уиджан', 'уирка', 'уисааль', 'улита', 'ульфат', 'ульяна', 'умара', 'умида', 'ундина', 'урания', 'урсула', 'устинья', 'фаатин', 'фавста', 'фадуа', 'фадыля', 'фаиза', 'фаина', 'фаляк', 'фарида', 'фариха', 'фатима', 'фатина', 'фатыма', 'фаузия', 'фаустина', 'фаэтуза', 'феба', 'феврония', 'февронья', 'федора', 'федосья', 'фекла', 'феклиста', 'фекуса', 'феликсана', 'фелицата', 'фелицитата', 'фелиция', 'феодора', 'феодосия', 'феодотия', 'феодулия', 'феозва', 'феоктиста', 'феона', 'феопистия', 'феофания', 'феофила', 'фервуфа', 'фермодесса', 'фессалоникия', 'фетида', 'фива', 'фивея', 'фида', 'филадельфия', 'филина', 'филиппия', 'филомена', 'филонилла', 'фирдаус', 'фируза', 'фиряль', 'флавия', 'флора', 'флорентина', 'флоренция', 'флориана', 'фомаида', 'фооса', 'фотина', 'фредерика', 'фрида', 'хаадия', 'хавля', 'хадиджа', 'хадийя', 'хадича', 'хадия', 'хайрийя', 'хайфа', 'хайям', 'хайят', 'халида', 'халима', 'халя', 'хамида', 'хана', 'ханан', 'ханийя', 'ханифа', 'хариесса', 'харита', 'харитина', 'хасна', 'хая', 'хельга', 'хесса', 'хинд', 'хиония', 'хлорида', 'хлоя', 'хриса', 'хрисеида', 'хрисия', 'христина', 'христодула', 'худа', 'хулюк', 'хума', 'хурийя', 'хусн', 'цвета', 'целеиа', 'цецелия', 'цецилия', 'цирцея', 'чеслава', 'чулпан', 'шаадия', 'шарифа', 'шарлотта', 'шатха', 'ширин', 'шушаника', 'эвандра', 'эвелина', 'эвридика', 'эвриклея', 'эвринома', 'эдита', 'эдна', 'электра', 'элеонора', 'элиза', 'элина', 'эльвина', 'эльвира', 'эльза', 'эльмира', 'эмилиан', 'эмилия', 'эмма', 'энона', 'эпикаста', 'эрида', 'эрика', 'эриния', 'эсмеральда', 'эстер', 'эя', 'юдифь', 'юлиана', 'юлиания', 'юлита', 'юлитта', 'юлия', 'юманита', 'юмн', 'юния', 'юнона', 'юсраа', 'юстина', 'ядвига', 'яна', 'ярослава', 'ясира', 'ясмин', 'яфьях'])

In [23]:
stops_antela = set(['1', '2', '3', '4', '5', '6', '7', '8', '9', '0', 'один', 'два', 'три', 'четыре', 'пять', 'шесть', 'семь', 'восемь', 'девять', 'ноль'])

In [24]:
with open('расширенный - вордстат.txt', 'r', encoding = 'UTF-8') as f:
    wrds = f.readlines()
    stops_ws = set(wrds)

with open('расширенный список.txt', 'r', encoding = 'UTF-8') as fl:
    wrds_1 = fl.readlines()
    stops_wr = set(wrds_1)

In [25]:
stops_big = set.union(stops_y, stops_new, stops_antela, stops_ws, stops_wr)

In [26]:
len(stops_big)

3677

In [28]:
for text in texts_cl_eng:
    for word in text:
        flg = 0
        #for el in word:
            #if el in eng_str:
                #flg = 1
        if len(word) == 1:
            flg = 1
        if 'lt;' in word:
            flg = 1
        if word in stops_big:
            flg = 1
        if not word.isalpha():
            flg = 1

            
        if flg == 1:
            text.remove(word)


In [31]:
%%time
lda_model_eng = lda_mod(texts_cl_eng)

CPU times: user 3min 36s, sys: 2min 41s, total: 6min 17s
Wall time: 4min 7s


In [32]:
res_bad = lda_model_eng.print_topics()

res_good = []
for word in res_bad:
    res = re.findall('\*"(.*?)"', word[1])
    res_good.append(res)
pd.DataFrame(res_good).T

0                      1        2                   3   \
0    объект                 сервер    товар               шарик   
1     метод                 клиент    канал       шанс_выиграть   
2  свойство                 сервис  продажа              печень   
3   атрибут                хостинг  реклама               удача   
4     класс                 облако   письмо  интуитивно_понятно   
5  значение                 услуга     цена               «нуть   
6    return         восстановление     сайт             выпасть   
7    public           оборудование   клиент    заработный_плата   
8    задать              база_дать     пост         случайность   
9      null  резервный_копирование  правило              reduce   

              4               5         6            7            8   \
0           боль          пароль    память        слайд         сеть   
1      изменение           yahoo  значение         мфть       доступ   
2  сопротивление      уязвимость     адрес      учебник     интернет   
3    определение          austin      байт          tdd       услуга   
4           тело       программа    запись  организатор     протокол   
5    происходить   visual_studio       int       читать        точка   
6          ткань       microsoft   регистр        опрос  подключение   
7       ситуация  учётный_запись       amp  публиковать      сетевой   
8          костя          сделка         1  комментарий       сервер   
9       организм           взлом       spi      далёкий   внутренний   

                9                 10          11               12        13  \
0    namespace_use            датчик    кампания             курс     стиль   
1         прибытие            корпус  объявление          студент   пиксель   
2        раскладка           питание   заголовок           лекция       css   
3             enum             плата      сервис  образовательный  значение   
4  продолжительный       температура      группа            group    ширина   
5         2013_год        контроллер     перенос         обучение       dom   
6      февраль_год           обычный      python    преподаватель    размер   
7             ipfs             режим      формат        программа   элемент   
8              «на           станция        ключ        помещение   область   
9  набирать_оборот  профессиональный      символ             null     color   

             14                    15           16           17  \
0         точка       ток_потребление   устройство       запрос   
1  пространство  любезно_предоставить   инструмент       ошибка   
2      источник           этаж_здание   синтезатор       сервер   
3    расстояние                максим         звук       размер   
4         поезд           скептически  современный         сайт   
5      движение    новогодний_подарок  разработать    обработка   
6      значение                safety         вода     обратный   
7     двигаться             structure       фильтр         ядро   
8            её      действующий_лицо    советский  оптимизация   
9        теория             flussonic    помещение  кэширование   

                      18                19  
0                    bmc             money  
1  предсказывать_будущее               nfc  
2                 summit       буфер_обмен  
3                   ipmi  интернет-магазин  
4                     dm        sys_import  
5                printer    накопитель_ssd  
6              раскрытый            список  
7    картинка_изобразить         отдельный  
8              программа         программа  
9                 список             метод

- надо убрать кавычки, которые плохо отделились
- убрать цифры
- убрать слова на латинице, чтобы не вылезало лишнего

In [37]:
texts_cl_no_eng = texts_cl_eng

In [34]:
num_str = '1234567890'

In [42]:
l = ['«vf', 'jg']
for n,w in enumerate(l):
    if '«' or '»' in w:
        l[n] = re.sub('[«»]', '', w)

l

['vf', 'jg']

In [50]:
for text in texts_cl_no_eng:
    for n, word in enumerate(text):
        flg = False
        
        if '«' or '»' in word:
            word = re.sub('[«»]', '', word)
            text[n] = word
        
        for el in word:
            if el in eng_str:
                #print(word)
                flg = True
            if el in num_str:
                #print(word)
                flg = True
        if len(word) == 1:
            flg = True
            #print(word)
        
        if not word.isalpha():
            flg = True
            #print(word)

            
        if flg:
            text.remove(word)


In [51]:
%%time
lda_model_no_eng = lda_mod(texts_cl_no_eng)

CPU times: user 3min 1s, sys: 2min 14s, total: 5min 15s
Wall time: 3min 24s


In [52]:
res_bad = lda_model_no_eng.print_topics()

res_good = []
for word in res_bad:
    #print(word[1])
    res = re.findall('\*"(.*?)"', word[1])
    #print(res)
    res_good.append(res)
pd.DataFrame(res_good).T

0           1                 2         3   \
0        услуга  библиотека              мозг      сайт   
1        клиент      тысяча           студент    клиент   
2      ценность       сумма           ребёнок  страница   
3       принцип     крупный             жизнь   реклама   
4      понятный   заплатить  программирование   продажа   
5      передача       книга       программист    трафик   
6     провайдер      бизнес           область      сеть   
7  поддерживать   компьютер          обучение   партнёр   
8    внутренний   сотрудник          развитие     канал   
9       каталог        день      исследование   покупка   

                       4            5                         6   \
0             южный_корея    двигатель                   джейсон   
1                   корея      спутник                 скопление   
2                сингапур       запуск                   дмитрий   
3                   южный  космический  стэнфордский_университет   
4             занять_ниша         план                     фишер   
5                    чили      причина                     литий   
6       игровой_индустрия         пуск          уровень_изоляция   
7                интернет     проверка                неизменный   
8  потенциальный_инвестор       орбита                 приняться   
9            физика_химия     провести          аркадный_автомат   

             7            8                            9   \
0    устройство     понимать                     бактерия   
1  перезагрузка        слово                  выращивание   
2    обновление         язык                    избавлять   
3         режим       думать                микроорганизм   
4        раздел       знание                 рад_услышать   
5        флешек      считать                      глонасс   
6      загрузка        книга  противоположный_направление   
7        старый       понять              солнечный_ветер   
8       консоль        жизнь                    пятьдесят   
9          диск  программист               магнитный_поль   

                     10                          11             12  \
0                фигура                    анимация           боль   
1         шанс_выиграть              ложиться_плечо      изменение   
2                партия           вполне_приемлемый  сопротивление   
3                   ход  синтаксический_конструкция    определение   
4                взятие                     элемент    происходить   
5       набирать_оборот                        либо          ткань   
6            продлиться                     переход           тело   
7                 шасси                  удержаться       ситуация   
8  минимизировать_риска                    значение       организм   
9               позиция                  однотипный       принятие   

                   13                14                     15  \
0              сервер              курс                прогноз   
1              запрос            лекция  индивидуальный_подход   
2              сервис           студент         взаимодействие   
3           поддержка     собеседование                 анализ   
4            нагрузка             билет                 помочь   
5           серверный          алгоритм              проводить   
6               пакет         подтянуть              поведение   
7             быстрый  программирование                  сфера   
8           база_дать              хайп                 модель   
9  производительность             отбор             предлагать   

                     16          17             18              19  
0                 фильм      машина     январь_год             соц  
1                рекорд       товар         сделка         скачать  
2               быстрый      прибор  расследование             хаб  
3                страна  автомобиль          взлом    обсерватория  
4                   маг      скидка       миллиард         request  
5              давление       

### 4) постройте несколько LDA моделей (переберите количество тем, можете поменять eta, alpha, passes), если получаются плохие темы, поработайте дополнительно над предобработкой и словарем;

In [54]:
%%time
lda_model_1 = lda_mod(texts_cl_no_eng, passes=10, num_topics=20)

CPU times: user 2min 34s, sys: 1min 22s, total: 3min 57s
Wall time: 2min 47s


In [55]:
res_bad = lda_model_1.print_topics()

res_good = []
for word in res_bad:
    #print(word[1])
    res = re.findall('\*"(.*?)"', word[1])
    #print(res)
    res_good.append(res)
pd.DataFrame(res_good).T

0           1            2          3          4           5   \
0       файл      услуга  температура     объект      атака     элемент   
1        бот    вакансия     скорость      класс      товар      модель   
2  сообщение       рынок   устройство      метод  сотрудник    значение   
3      канал      страна       корпус   свойство     пароль        цикл   
4      поиск    интернет  аккумулятор    атрибут  вселенная      память   
5     сервис      клиент       печать     модуль     доступ      размер   
6      релиз      доступ          дом   значение   инцидент       слово   
7     письмо  российский      питание   контекст    причина    операция   
8      видео    документ      головка  структура  известный  библиотека   
9   название      защита     мощность     задать  поскольку        язык   

                 6         7         8          9            10  \
0           студент      игра      сайт       файл  изображение   
1              курс     игрок    сервер   добавить        точка   
2         программа   игровой     домен   страница       сигнал   
3       программист        её    сервис  компонент   координата   
4              день    играть    ссылка   параметр     значение   
5              язык     карта    трафик  сообщение       машина   
6  программирование  дизайнер  страница  настройка      яркость   
7             книга   история    клиент     скрипт     алгоритм   
8            читать    деньга      сеть     строка         цвет   
9        рассказать     удача    машина      папка       прибор   

              11             12          13         14            15  \
0     устройство           мозг      бизнес     клетка      заказчик   
1           звук        область    открытый     учёный       продукт   
2      усилитель   исследование       робот  двигатель       продажа   
3           цена           лицо    цифровой     страна        клиент   
4         камера        ребёнок      ресурс      земля       реклама   
5        телефон  исследователь     область       тело        деньга   
6       смартфон    изображение       набор   материал       перевод   
7  производитель        пациент  публикация    энергия          цель   
8     инструмент     инструмент       смысл    причина  тестирование   
9   производство       младенец        счёт       кожа        тысяча   

           16          17          18            19  
0     браузер      запрос        сеть          игра  
1  устройство      массив      сервер          боль  
2  обновление     условие     правило         игрок  
3      модель      запись      доступ  исследование  
4      клиент      строка  устройство        понять  
5   платформа   база_дать        узел          тест  
6   мобильный  репликация     событие        играть  
7      сервис     таблица   настройка     изменение  
8   изменение   выражение       пакет        почему  
9     будущее      индекс        база      понимать

In [56]:
%%time
lda_model_1 = lda_mod(texts_cl_no_eng, passes=10, num_topics=30)

CPU times: user 2min 50s, sys: 1min 53s, total: 4min 44s
Wall time: 3min 9s


In [57]:
res_bad = lda_model_1.print_topics()

res_good = []
for word in res_bad:
    #print(word[1])
    res = re.findall('\*"(.*?)"', word[1])
    #print(res)
    res_good.append(res)
pd.DataFrame(res_good).T

0              1           2             3            4   \
0       печать          атака       книга    устройство    платформа   
1     скорость     библиотека      читать        раздел  архитектура   
2  температура          закон       жизнь         режим       сервис   
3      головка     российский  заниматься  перезагрузка   инструмент   
4     материал      компьютер       ничто        флешек    поддержка   
5      принтер         пароль      вообще    обновление       модель   
6       деталь         доступ      думать      загрузка   библиотека   
7      изделие        крупный    пытаться          диск       подход   
8      пластик   безопасность    понимать     выполнить     облачный   
9           мм  представитель        день       выбрать         язык   

              5                 6            7           8         9   \
0           боль         программа         сеть      сервер    массив   
1      изменение  программирование       доступ       домен    объект   
2  сопротивление       программист     интернет      скрипт     класс   
3           тело         компьютер        точка        сайт  значение   
4    определение           студент  подключение   настройка     метод   
5    происходить              язык        актор      сервис  контекст   
6       ситуация       электроника  конференция   установка    строка   
7          ткань            знание    публичный      ссылка      цикл   
8           рука           задание       клетка  установить     вызов   
9       организм           предмет    сообщение      машина   условие   

            10            11            12         13             14  \
0  изображение       яркость          игра       файл           мозг   
1     алгоритм      стандарт         игрок    браузер   исследование   
2        точка        сигнал        играть        бот         учёный   
3      элемент  пространство       игровой      канал        область   
4     значение          цвет  исследование      поиск           лицо   
5       объект       частота        понять       язык  исследователь   
6      область      диапазон      дизайнер  сообщение        пациент   
7         блок      основный            её    перевод       младенец   
8       размер      параметр          тест   название        ребёнок   
9      граница      источник         часто     группа          метод   

             15           16           17          18              19  
0        услуга   устройство       страна       слово            тест  
1      вакансия         звук    двигатель    кампания            узел  
2        клиент       машина        робот       текст            сеть  
3        сервер     смартфон      энергия      строка  вычислительный  
4          сайт        режим     скорость      символ            ядро  
5          опыт  аккумулятор        земля        файл        операция  
6      ценность    усилитель          сша  объявление        скорость  
7  поддерживать       корпус  южный_корея   заголовок        задержка  
8      понятный  температура     интернет      стикер       процессор  
9        анализ          дом      причина      дерево       сообщение

In [58]:
%%time
lda_model_1 = lda_mod(texts_cl_no_eng, passes=20, num_topics=25)

CPU times: user 3min 46s, sys: 2min 46s, total: 6min 32s
Wall time: 3min 59s


In [59]:
res_bad = lda_model_1.print_topics()

res_good = []
for word in res_bad:
    #print(word[1])
    res = re.findall('\*"(.*?)"', word[1])
    #print(res)
    res_good.append(res)
pd.DataFrame(res_good).T

0           1            2          3             4           5   \
0       файл      услуга  температура     объект         атака    значение   
1  сообщение    вакансия   устройство      класс         товар     элемент   
2        бот       рынок     скорость      метод     сотрудник        цикл   
3      канал      страна       корпус   свойство        пароль      память   
4      поиск      клиент       печать    атрибут     вселенная       слово   
5     письмо    интернет  аккумулятор     модуль        доступ      размер   
6      отчёт  российский          дом   значение     известный        язык   
7     сервис      доступ      питание   контекст       причина        блок   
8      видео    документ       датчик  структура  безопасность  библиотека   
9   название      защита     мощность      вызов       попытка      строка   

                 6         7         8          9             10  \
0           студент      игра      сайт       файл   изображение   
1              курс     игрок    сервер   добавить         точка   
2         программа   игровой     домен   страница        сигнал   
3              день        её    сервис  компонент    координата   
4       программист    играть    клиент   параметр        машина   
5              язык     карта    трафик  настройка      значение   
6            читать  дизайнер  страница  сообщение       яркость   
7             книга   история    ссылка     скрипт      алгоритм   
8        рассказать    думать      сеть     список  пространство   
9  программирование    деньга   партнёр      папка          цвет   

              11             12          13         14            15  \
0     устройство           мозг      бизнес     учёный       продукт   
1           звук        область    открытый     клетка      заказчик   
2         камера   исследование       робот  двигатель       продажа   
3           цена           лицо    цифровой      земля       перевод   
4        телефон        ребёнок      ресурс     страна        клиент   
5       смартфон  исследователь     область    энергия          цель   
6      усилитель    изображение   сотрудник       тело         текст   
7  производитель       обучение        счёт   материал  тестирование   
8          экран        пациент       набор    причина       реклама   
9     инструмент     инструмент  публикация    спутник   комментарий   

           16           17           18            19  
0     браузер       запрос         сеть          игра  
1      модель       массив       сервер          боль  
2  устройство      условие      правило         игрок  
3  обновление       запись       доступ          тест  
4      клиент    база_дать   устройство  исследование  
5   мобильный    выражение         узел        понять  
6      сервис   репликация        пакет        играть  
7   платформа  архитектура      событие     изменение  
8   изменение       строка    настройка        почему  
9      сервер      таблица  виртуальный   происходить

#### Не плохо, надо еще что-то изменить

In [65]:
%%time
lda_model_1 = lda_mod(texts_cl_no_eng, passes=20, num_topics=25, no_above = 0.25)

CPU times: user 3min 57s, sys: 3min 3s, total: 7min 1s
Wall time: 4min 7s


In [66]:
res_bad = lda_model_1.print_topics()

res_good = []
for word in res_bad:
    #print(word[1])
    res = re.findall('\*"(.*?)"', word[1])
    #print(res)
    res_good.append(res)
pd.DataFrame(res_good).T

0            1              2           3               4   \
0      бизнес  температура         камера     элемент          сервер   
1       рынок       печать         модель      строка         событие   
2      деньга     скорость          экран      запрос         правило   
3    заказчик     материал       смартфон     таблица          клиент   
4      клиент       корпус           цена        цикл  инфраструктура   
5     крупный      головка        телефон      запись          сервис   
6      услуга        плата          товар        блок          запрос   
7     продажа      питание          видео  переменный        облачный   
8   сотрудник      принтер  производитель     условие        нагрузка   
9  российский       сигнал      процессор   компонент       поддержка   

                            5           6         7           8   \
0                 безопасность      думать      мозг      модуль   
1                       доступ     продукт     поиск      скрипт   
2                        атака  самый_дело   ребёнок      раздел   
3                       защита    довольно    клетка    загрузка   
4                   уязвимость    смотреть      лицо       папка   
5                  организация     далёкий  младенец       режим   
6                       пароль    хотеться    музыка  обновление   
7                     интернет    примерно     канал   запустить   
8                    сотрудник        пара     релиз   настройка   
9  информационный_безопасность       взять  развитие      пароль   

             9            10             11           12       13         14  \
0     двигатель     контекст          текст  изображение     часы   страница   
1   аккумулятор   библиотека           язык      шорткат    город  сообщение   
2       батарея        вызов        перевод       стикер   сервис    браузер   
3     помещение        класс         дизайн      область   машина     ссылка   
4  оборудование    структура  рабочий_место     алгоритм   сервер      домен   
5  производство         тест       цифровой  электроника   квеста    контент   
6      провести       объект        спутник      задание     план        бот   
7      проверка       подход       название     выделить      час      форма   
8       ёмкость       логика    локализация        класс  загадка     дефект   
9          план  рефакторинг         ракета      граница    месяц  добавлять   

           15            16                17        18            19  
0      объект      вакансия           студент      сеть          боль  
1      массив        анализ              курс    услуга        учёный  
2       класс  тестирование       программист    трафик  исследование  
3    свойство       область             книга    доступ       энергия  
4     атрибут        группа  программирование    клиент       научный  
5      задать          опыт        рассказать  интернет          тело  
6        поль      гипотеза       конференция  протокол         земля  
7  реализация   тестировщик          участник     точка        страна  
8  определять          язык              тема     канал      скорость  
9      ссылка       выборка            знание  передача         жизнь

In [67]:
lda_model_1.print_topics(25)

[(0,
  '0.014*"сервер" + 0.012*"пакет" + 0.011*"ядро" + 0.011*"узел" + 0.011*"сеть" + 0.010*"контейнер" + 0.009*"адрес" + 0.009*"настройка" + 0.009*"порт" + 0.008*"тест"'),
 (1,
  '0.053*"сеть" + 0.041*"услуга" + 0.021*"трафик" + 0.020*"доступ" + 0.020*"клиент" + 0.017*"интернет" + 0.014*"протокол" + 0.012*"точка" + 0.011*"канал" + 0.010*"передача"'),
 (2,
  '0.022*"двигатель" + 0.014*"аккумулятор" + 0.012*"батарея" + 0.011*"помещение" + 0.009*"оборудование" + 0.008*"производство" + 0.007*"провести" + 0.007*"проверка" + 0.007*"ёмкость" + 0.006*"план"'),
 (3,
  '0.010*"часы" + 0.010*"город" + 0.009*"сервис" + 0.009*"машина" + 0.009*"сервер" + 0.009*"квеста" + 0.009*"план" + 0.008*"час" + 0.008*"загадка" + 0.008*"месяц"'),
 (4,
  '0.014*"контекст" + 0.014*"библиотека" + 0.014*"вызов" + 0.013*"класс" + 0.013*"структура" + 0.010*"тест" + 0.010*"объект" + 0.010*"подход" + 0.008*"логика" + 0.007*"рефакторинг"'),
 (5,
  '0.021*"изображение" + 0.018*"шорткат" + 0.012*"стикер" + 0.012*"область"

### 5) для самой хорошей модели в отдельной ячейке напечатайте 3 хороших (на ваш вкус) темы

Кажется, лучше всего вышло при passes=20, num_topics=25, no_above = 0.25

- НАСТРОЙКА СЕРВЕРА (0,
  '0.014*"сервер" + 0.012*"пакет" + 0.011*"ядро" + 0.011*"узел" + 0.011*"сеть" + 0.010*"контейнер" + 0.009*"адрес" + 0.009*"настройка" + 0.009*"порт" + 0.008*"тест"'),
- ИНТЕРНЕТ-СОЕДИНЕНИЕ (1,
  '0.053*"сеть" + 0.041*"услуга" + 0.021*"трафик" + 0.020*"доступ" + 0.020*"клиент" + 0.017*"интернет" + 0.014*"протокол" + 0.012*"точка" + 0.011*"канал" + 0.010*"передача"')
 
- ИНФОРМАЦИОННАЯ БЕЗОПАСНОСТЬ (21,
  '0.018*"безопасность" + 0.013*"доступ" + 0.012*"атака" + 0.012*"защита" + 0.011*"уязвимость" + 0.007*"организация" + 0.007*"пароль" + 0.007*"интернет" + 0.007*"сотрудник" + 0.006*"информационный_безопасность"')

### 6) между словарем и обучением модели добавьте tfidf (gensim.models.TfidfModel(corpus, id2word=dictionary); corpus = tfidf[corpus]);

Это мы уже сделали: в функции lda_mod есть возможность сделать tf-idf

### 7) повторите пункт 4 на преобразованном корпусе;

In [68]:
%%time
lda_model_1 = lda_mod(texts_cl_no_eng, passes=10, num_topics=20, tfidf=True)

CPU times: user 4min 5s, sys: 1min 19s, total: 5min 24s
Wall time: 4min 30s


In [69]:
res_bad = lda_model_1.print_topics()

res_good = []
for word in res_bad:
    #print(word[1])
    res = re.findall('\*"(.*?)"', word[1])
    #print(res)
    res_good.append(res)
pd.DataFrame(res_good).T

0                      1                2               3   \
0        игра  согласование_документ          шорткат  второе_квартал   
1        файл                   игра        хромосома  деление_клетка   
2      сервер                 объект  ёмкость_батарея              чд   
3  устройство                   файл         хостовый            игра   
4        сайт                  класс             игра          объект   
5        сеть                элемент           объект            файл   
6     браузер             устройство             файл           класс   
7      сервис               значение            класс         элемент   
8      услуга                 сервер          элемент      устройство   
9      клиент                 модель       устройство        значение   

                   4                    5                            6   \
0                 фас                 игра                   синтезатор   
1  цифровой_экономика               объект              порекомендовать   
2          деструктор                 файл  профессиональный_литература   
3                игра  лишний_телодвижение                  многое_друг   
4              объект                класс           интересно_выяснить   
5                файл              элемент            лайфхак_позволять   
6      договорённость           устройство                   труд_отдых   
7             command             значение     репозиторий_пользоваться   
8               класс               сервер    профессиональный_привычка   
9             элемент               модель         общий_закономерность   

               7           8              9                       10  \
0       усилитель         чен  капитализация  балансировщик_нагрузка   
1     температура        игра           игра                    игра   
2         яркость      объект         объект                  объект   
3          корпус        файл           файл                    файл   
4         зарядка       класс          класс                   класс   
5           робот     элемент        элемент                 элемент   
6           пилот  устройство     устройство              устройство   
7       вселенная    значение       значение                значение   
8  магнитный_поль      сервер         сервер                  сервер   
9     аккумулятор      модель         модель                  модель   

                          11          12          13          14  \
0    независимый_объективный    младенец       актор        игра   
1             автор_желающий        игра        игра      объект   
2       радость_предоставить      объект      объект        файл   
3              даджет_блогер        файл        файл       класс   
4  заинтересовать_публикация        шелл       класс     элемент   
5               обзор_даджет       класс     элемент  устройство   
6        уточнить_информация     элемент  устройство    значение   
7       предотвратить_ошибка  устройство    значение      сервер   
8      оставаться_усмотрение    значение      модель      модель   
9                       игра      сервер      сервер    страница   

                   15             16                17          18          19  
0                 фсб    южный_корея             табло      объект        игра  
1        законопроект          слайд              реле      массив      объект  
2           ведомство           прям          резистор       класс        файл  
3       сообщать_тасс         датчик          unsigned     атрибут       класс  
4                игра      двигатель              игра   компонент     элемент  
5              объект           пуск            объект    свойство  устройство  
6                файл        спутник               щит  репликация    значение  
7  федеральный_служба        вносить              файл        файл      сервер  
8               ридер         ракета       выключаться    значение      модель  
9               класс  фоновы

In [70]:
%%time
lda_model_1 = lda_mod(texts_cl_no_eng, passes=10, num_topics=30, tfidf=True)

CPU times: user 4min 14s, sys: 1min 40s, total: 5min 55s
Wall time: 4min 47s


In [71]:
res_bad = lda_model_1.print_topics()

res_good = []
for word in res_bad:
    #print(word[1])
    res = re.findall('\*"(.*?)"', word[1])
    #print(res)
    res_good.append(res)
pd.DataFrame(res_good).T

0                     1                       2   \
0        уточнить_информация    цифровой_экономика             гендиректор   
1    независимый_объективный            подать_суд              твиттереть   
2               обзор_даджет               вторник   обучение_подкрепление   
3       радость_предоставить         ликвидировать          бумажный_книга   
4              даджет_блогер       авторский_право  интеллектуальный_агент   
5             автор_желающий                бедный                    сайт   
6  заинтересовать_публикация                    чд                 продукт   
7       предотвратить_ошибка      требование_выкуп                    файл   
8      оставаться_усмотрение  аппаратный_ускорение                  сервер   
9             россия_украина  потенциальный_жертва                   книга   

                      3             4                   5   \
0                  корея      инцидент    партнерский_сеть   
1  постараться_объяснить     усилитель                 соц   
2  предсказывать_будущее   южный_корея           квестовый   
3                 трение  законопроект      чистый_прибыль   
4           стабилизатор           фсб             покемон   
5          декодирование            рф             дискета   
6               истинный      гибкость  хранение_резервный   
7                  вт_вт         закон       лекция_лекция   
8             сша_канада        услуга                  лм   
9              коптереть  безопасность    платный_подписка   

                             6         7                      8   \
0        операционный_усилитель      игра              конвертер   
1                          фмрт     игрок                  логин   
2               краткий_экскурс  контекст  вредоносный_программа   
3                   возбуждение      мозг                субъект   
4                          шелл   студент          ниже_рыночный   
5          плотность_размещение  заказчик                   виза   
6              ребёнок_взрослый      курс    новогодний_праздник   
7               нервный_волокно     книга  регулярно_обновляться   
8                         эйлер   продажа            выключатель   
9  двухфакторный_аутентификация   ребёнок             копировать   

                      9                    10                  11  \
0            поляризация                слайд           хромосома   
1                  ридер        регулирование      магнитный_поль   
2               роговица          иллюстрация            сетчатка   
3  клинический_испытание     самообслуживание              блогер   
4                раковый  программный_комитет      деление_клетка   
5           фильм_сериал          долгий_ящик             счётчик   
6     негативный_влияние        номер_телефон             фонарик   
7                 печень             поправка                 щит   
8          петербургский   подробно_разбирать  напряжение_питание   
9                 format            поспорить               резка   

                         12                                13            14  \
0                  младенец                        синтезатор          last   
1            второе_квартал            балансировщик_нагрузка      мгту_имя   
2                  беларусь                     присоединение           вич   
3           ёмкость_батарея                     балансировщик  молекула_днк   
4  функциональный_парадигма                            result   масса_тонна   
5                 арифметик                           options       вакцина   
6            географический                   продолжительный         пират   
7                     игорь                          unsigned          сайт   
8          заработный_плата                            протез       продукт   
9              сыграть_роль  восстановление_работоспособность          файл   

                        15                  16                      17  \
0          выпадать_список     

In [74]:
%%time
lda_model_1 = lda_mod(texts_cl_no_eng, passes=20, num_topics=25, tfidf=True)

CPU times: user 6min 57s, sys: 3min 4s, total: 10min 2s
Wall time: 7min 36s


In [75]:
res_bad = lda_model_1.print_topics()

res_good = []
for word in res_bad:
    #print(word[1])
    res = re.findall('\*"(.*?)"', word[1])
    #print(res)
    res_good.append(res)
pd.DataFrame(res_good).T

0                       1                  2            3   \
0                 фас  балансировщик_нагрузка         устройство  температура   
1          устройство              устройство             сервер  аккумулятор   
2              сервер                  сервер  силовой_установка    усилитель   
3      читать_слушать                    сайт               сайт     инцидент   
4                сайт                    сеть               сеть       кабель   
5  федеральный_служба               компьютер          компьютер        китай   
6                сеть                  модель             модель        актор   
7           компьютер                  сервис           проехать       дефект   
8              модель                  машина             сервис       корпус   
9              сервис               программа             машина      шорткат   

                4            5                  6                7   \
0  базовый_станция   устройство          технопарк            слайд   
1    ниже_рыночный       сервер         устройство           читать   
2               чд         сайт             сервер         подборка   
3       устройство         сеть         деструктор      иллюстрация   
4           сервер    компьютер  университет_итмый       переводить   
5             сайт       модель               сайт      публиковать   
6             сеть       сервис               сеть  порекомендовать   
7        компьютер       машина          компьютер            опрос   
8           модель    программа             модель        типизация   
9           сервис  виртуальный             сервис          перевод   

            8                        9                      10  \
0   устройство  система_видеонаблюдение                  табло   
1       сервер       цифровой_экономика       партнерский_сеть   
2         сайт               устройство             устройство   
3         сеть                   сервер                 сервер   
4    компьютер                     сайт                   сайт   
5       модель                     сеть  примечание_переводчик   
6       сервис                компьютер                   сеть   
7       машина                   модель              компьютер   
8    программа                   сервис                 модель   
9  виртуальный                   ночное                 сервис   

               11         12          13           14            15  \
0  второе_квартал       файл  устройство   устройство          игра   
1      устройство     сервер      сервер       сервер        услуга   
2          сервер     объект        сайт         сайт          сайт   
3            сайт    браузер        сеть         сеть       продукт   
4   сообщать_тасс     запрос    роговица    компьютер          сеть   
5            сеть      класс   компьютер       модель         игрок   
6       компьютер  компонент      модель       сервис        клиент   
7          модель     строка      сервис       машина     сотрудник   
8          сервис  сообщение      машина    программа    устройство   
9          машина   значение   программа  виртуальный  безопасность   

            16           17           18             19  
0   устройство   синтезатор   устройство     устройство  
1       сервер  магнитометр       сервер         сервер  
2         сайт   устройство         сайт  учёт_инфляция  
3         сеть       сервер         сеть           сайт  
4    компьютер      головка    компьютер           сеть  
5       модель         сайт       модель      компьютер  
6       сервис         сеть       сервис         модель  
7       машина    компьютер       машина         сервис  
8    программа       модель    программа         машина  
9  виртуальный       сервис  виртуальный      программа

In [76]:
%%time
lda_model_1 = lda_mod(texts_cl_no_eng, passes=20, num_topics=25, no_above = 0.25, tfidf=True)

CPU times: user 6min 34s, sys: 2min 45s, total: 9min 20s
Wall time: 7min 10s


In [77]:
res_bad = lda_model_1.print_topics()

res_good = []
for word in res_bad:
    #print(word[1])
    res = re.findall('\*"(.*?)"', word[1])
    #print(res)
    res_good.append(res)
pd.DataFrame(res_good).T

0              1              2              3   \
0  согласование_документ           игра           игра           игра   
1          ниже_рыночный         клиент         клиент         клиент   
2                   игра         сервис         сервис         сервис   
3                 клиент        продукт        продукт        продукт   
4                 сервис          книга          книга          книга   
5                продукт         модель         модель         модель   
6                  книга      компьютер      компьютер      компьютер   
7                 модель  производитель  производитель  производитель   
8              компьютер           язык           язык           язык   
9          производитель           сеть           сеть           сеть   

          4                  5              6                            7   \
0     сервер                лвс            фас              порекомендовать   
1     объект     второе_квартал      регулятор                        книга   
2     запрос                 рн  производитель  профессиональный_литература   
3      класс               игра     подать_суд                  многое_друг   
4  сообщение             клиент          штраф               помочь_выявить   
5       сеть             сервис             рф                   труд_отдых   
6  компонент            продукт         январь     репозиторий_пользоваться   
7   страница  двигатель_ступень     корпорация           интересно_выяснить   
8     модуль              книга            суд            лайфхак_позволять   
9     модель             модель     российский    профессиональный_привычка   

             8                          9            10             11  \
0          игра              даджет_блогер         игра             чд   
1        услуга  заинтересовать_публикация          бот           игра   
2     сотрудник    независимый_объективный         звук         клиент   
3         игрок             автор_желающий     смартфон         сервис   
4        бизнес       радость_предоставить  аккумулятор        продукт   
5  безопасность               обзор_даджет      реклама          книга   
6        страна        уточнить_информация     вакансия         модель   
7      заказчик       предотвратить_ошибка   мессенджер      компьютер   
8  исследование      оставаться_усмотрение    усилитель  производитель   
9          мозг                       игра          дом           язык   

              12             13                     14  \
0           игра           игра                  табло   
1         клиент         клиент                   реле   
2         сервис         сервис           оборудование   
3        продукт        продукт                 услуга   
4          книга          книга               резистор   
5         модель         модель                аппарат   
6      компьютер      компьютер                 клиент   
7  производитель  производитель                 деньга   
8           язык           язык                 кнопка   
9           сеть           сеть  примечание_переводчик   

                       15             16             17              18  \
0  балансировщик_нагрузка           игра     синтезатор            кндр   
1                    игра         клиент           игра  читать_слушать   
2                  клиент         сервис         клиент        хостовый   
3                  сервис           шелл         сервис            игра   
4                 продукт        продукт        продукт          клиент   
5                   книга          книга          книга          сервис   
6                  модель         модель         модель         продукт   
7               компьютер      компьютер      компьютер           книга   
8           производитель  производитель  производитель          модель   
9                    язык           язык           язык       компьютер   

              19  
0           игра  
1         клиент  
2         с

In [78]:
lda_model_1.print_topics(25)

[(0,
  '0.001*"мбайт" + 0.001*"игра" + 0.001*"клиент" + 0.001*"сервис" + 0.001*"продукт" + 0.001*"плотность_размещение" + 0.001*"книга" + 0.001*"модель" + 0.001*"компьютер" + 0.001*"производитель"'),
 (1,
  '0.003*"кндр" + 0.001*"читать_слушать" + 0.001*"хостовый" + 0.001*"игра" + 0.001*"клиент" + 0.001*"сервис" + 0.001*"продукт" + 0.001*"книга" + 0.001*"модель" + 0.001*"компьютер"'),
 (2,
  '0.001*"даджет_блогер" + 0.001*"заинтересовать_публикация" + 0.001*"независимый_объективный" + 0.001*"автор_желающий" + 0.001*"радость_предоставить" + 0.001*"обзор_даджет" + 0.001*"уточнить_информация" + 0.001*"предотвратить_ошибка" + 0.001*"оставаться_усмотрение" + 0.001*"игра"'),
 (3,
  '0.001*"игра" + 0.001*"клиент" + 0.001*"сервис" + 0.001*"продукт" + 0.001*"книга" + 0.001*"модель" + 0.001*"компьютер" + 0.001*"производитель" + 0.001*"язык" + 0.001*"сеть"'),
 (4,
  '0.003*"игра" + 0.003*"бот" + 0.003*"звук" + 0.002*"смартфон" + 0.002*"аккумулятор" + 0.002*"реклама" + 0.002*"вакансия" + 0.002*"ме

### 8) в отдельной ячейке опишите как изменилась модель (приведите несколько тем, которые стали лучше или хуже, или которых раньше вообще не было; можно привести значения перплексии и когерентности для обеих моделей)

Смотрим на модель при passes=20, num_topics=25, no_above = 0.25:

Появились новые темы:
- (19,
  '0.006*"фас" + 0.002*"регулятор" + 0.001*"производитель" + 0.001*"подать_суд" + 0.001*"штраф" + 0.001*"рф" + 0.001*"январь" + 0.001*"корпорация" + 0.001*"суд" + 0.001*"российский"')


Но не всегда понятно, что за тема:
- (21,
  '0.004*"лвс" + 0.002*"второе_квартал" + 0.001*"рн" + 0.001*"игра" + 0.001*"клиент" + 0.001*"сервис" + 0.001*"продукт" + 0.001*"двигатель_ступень" + 0.001*"книга" + 0.001*"модель"'),


Несколько тем получились практически идентичны:
- 23,
  '0.001*"чд" + 0.001*"игра" + 0.001*"клиент" + 0.001*"сервис" + 0.001*"продукт" + 0.001*"книга" + 0.001*"модель" + 0.001*"компьютер" + 0.001*"производитель" + 0.001*"язык"'),
- (24,
  '0.002*"чен" + 0.001*"игра" + 0.001*"клиент" + 0.001*"сервис" + 0.001*"продукт" + 0.001*"книга" + 0.001*"модель" + 0.001*"компьютер" + 0.001*"производитель" + 0.001*"язык"')
- (15,
  '0.001*"игра" + 0.001*"клиент" + 0.001*"сервис" + 0.001*"продукт" + 0.001*"книга" + 0.001*"модель" + 0.001*"компьютер" + 0.001*"производитель" + 0.001*"язык" + 0.001*"сеть"'),
- (16,
  '0.001*"игра" + 0.001*"клиент" + 0.001*"сервис" + 0.001*"продукт" + 0.001*"книга" + 0.001*"модель" + 0.001*"компьютер" + 0.001*"производитель" + 0.001*"язык" + 0.001*"сеть"'),
- (17,
  '0.001*"игра" + 0.001*"клиент" + 0.001*"сервис" + 0.001*"продукт" + 0.001*"книга" + 0.001*"модель" + 0.001*"компьютер" + 0.001*"производитель" + 0.001*"язык" + 0.001*"сеть"'),
- (18,
  '0.001*"игра" + 0.001*"клиент" + 0.001*"сервис" + 0.001*"продукт" + 0.001*"книга" + 0.001*"модель" + 0.001*"компьютер" + 0.001*"производитель" + 0.001*"язык" + 0.001*"сеть"')


Почти во всех темах встречаются слова: __книга, игра, сервис__



### 9) проделайте такие же действия для NMF (образец в конце тетрадки), для построения словаря воспользуйтесь возможностями Count или Tfidf Vectorizer (попробуйте другие значение max_features, min_df, max_df, сделайте нграмы через ngram_range, если хватает памяти), попробуйте такие же количества тем

### Разложение матриц в sklearn

In [79]:
from sklearn.decomposition import NMF
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
import pandas as pd

Sklearn принимает на вход строки, поэтому склеим наши списки.

In [80]:
stexts = [' '.join(text) for text in texts_cl_no_eng]

In [91]:
def nmf_mod(stexts,
              n_components=10,
              alpha=0,
              max_features=25000,
              min_df=6,
              max_df=0.1,
              lowercase=False, 
              ngram_range=(1,1)):
        
    vectorizer = TfidfVectorizer(max_features=max_features,
                                 min_df=min_df,
                                 max_df=max_df,
                                 lowercase=lowercase,
                                 ngram_range=ngram_range)
    X = vectorizer.fit_transform(stexts)
    
    model = NMF(n_components=n_components, random_state=55, alpha=alpha)
    model.fit(X)
    
    return model, vectorizer

In [95]:
def get_nmf_topics(model, vectorizer, n_top_words):
    
    #id слов.
    feat_names = vectorizer.get_feature_names()
    
    word_dict = {};
    for i in range(model.n_components):
        
        #топ n слов для темы.
        words_ids = model.components_[i].argsort()[:-n_top_words - 1:-1]
        words = [feat_names[key] for key in words_ids]
        word_dict['Topic # ' + '{:02d}'.format(i+1)] = words;
    
    return pd.DataFrame(word_dict);

In [92]:
%%time
model, vectorizer = nmf_mod(stexts)

CPU times: user 4.97 s, sys: 824 ms, total: 5.8 s
Wall time: 5.9 s


In [96]:
get_nmf_topics(model, vectorizer, 10)

Topic # 01   Topic # 02  Topic # 03     Topic # 04   Topic # 05  \
0       массив  космический      сигнал     уязвимость       камера   
1       сборка      спутник        звук          атака     смартфон   
2       плагин       орбита     частота         пароль           гб   
3        папка        земля     наушник  злоумышленник  аккумулятор   
4       шаблон      аппарат   усилитель    вредоносный      дисплей   
5  репозиторий         марс       плата     шифрование       корпус   
6   возвращать      станция    диапазон        учётный       датчик   
7     аргумент      планета      музыка     сертификат    процессор   
8   компилятор    вселенная    звуковой        аккаунт      ноутбук   
9   директория         наса  напряжение          домен        рубль   

   Topic # 06   Topic # 07 Topic # 08  Topic # 09        Topic # 10  
0       игрок         мозг       диск         бот       конференция  
1     игровой       учёный     облако         чат            письмо  
2    персонаж        робот   облачный  мессенджер           реклама  
3    геймплей      пациент  резервный    телеграм              офис  
4        враг       клетка     трафик       токен          директор  
5        жанр    нейросеть    сетевой    отправка  профессиональный  
6  реальность      ребёнок    кластер       робот          менеджер  
7     комната      научный  процессор  сертификат           стартап  
8      движок    интеллект         вм        лига             товар  
9      миссия  университет  хранилище   аудитория        социальный

In [103]:
%%time
model, vectorizer = nmf_mod(stexts,n_components=20,ngram_range=(1,2))

CPU times: user 29.9 s, sys: 8.48 s, total: 38.4 s
Wall time: 32.6 s


In [104]:
get_nmf_topics(model, vectorizer, 10)

Topic # 01   Topic # 02   Topic # 03   Topic # 04  Topic # 05  \
0     реклама      пациент       плагин       камера    блокчейн   
1    заказчик         мозг        папка     смартфон  автомобиль   
2    менеджер       клетка       сборка           гб  финансовый   
3   аудитория       учёный  репозиторий  аккумулятор       банка   
4  социальный  заболевание   директория      дисплей      платёж   
5    дизайнер      болезнь    контейнер       корпус       закон   
6      письмо          ген         окно    процессор  транзакция   
7     контент         врач         меню      ноутбук    миллиард   
8   маркетинг      лечение       пароль       датчик        банк   
9     ребёнок     организм      каталог      батарея       доход   

            Topic # 06   Topic # 07     Topic # 08              Topic # 09  \
0      порекомендовать  космический     уязвимость                   игрок   
1         предпочитать      спутник          атака                 игровой   
2     профессиональный       орбита         пароль                персонаж   
3              слушать      аппарат  злоумышленник                    враг   
4               музыка         марс    вредоносный                геймплей   
5             бумажный        земля         ботнет                  миссия   
6    внутренний проект      станция         жертва                 комната   
7       бумажный книга         наса        учётный  виртуальный реальность   
8  электронный читалка         луна     шифрование              реальность   
9              читалка       ракета  исследователь                ваш игра   

   Topic # 10  Topic # 11  Topic # 12  Topic # 13     Topic # 14  Topic # 15  \
0         бот   вселенная      сигнал    анимация          робот      массив   
1         чат   галактика        звук    текстура        ребёнок   указатель   
2    телеграм     энергия     частота     пиксель         датчик  компилятор   
3  мессенджер      звезда     наушник      шейдёр  робототехника    аргумент   
4       токен     материя   усилитель        кадр           дрон  возвращать   
5        лига      тёмный       плата  координата     автомобиль      символ   
6    отправка      солнце    звуковой       сцена         сборка   выражение   
7     чат бот      теория    диапазон      спрайт          школа  анализатор   
8   текстовый   излучение      музыка        слой           узел        байт   
9      диалог  гравитация  напряжение      движок         дронов      индекс   

                Topic # 16      Topic # 17             Topic # 18  \
0                нейросеть           товар                   диск   
1                нейронный          скидка              резервный   
2           нейронный сеть         магазин     виртуальный машина   
3                интеллект      покупатель                     вм   
4                 машинный         покупка                 облако   
5            искусственный      распродажа                кластер   
6  искусственный интеллект           заказ               облачный   
7        машинный обучение           акция            копирование   
8                     слой        продавец                  бэкап   
9                   нейрон  чёрный пятница  резервный копирование   

     Topic # 19   Topic # 20  
0    сертификат  конференция  
1         домен       спикер  
2        письмо  выступление  
3        пароль       доклад  
4      почтовый        слайд  
5         токен  мероприятие  
6        трафик  презентация  
7  сертификация      встреча  
8    контроллер       москва  
9         почта      декабрь

In [105]:
%%time
model, vectorizer = nmf_mod(stexts,n_components=25,ngram_range=(1,2))

CPU times: user 50.3 s, sys: 26.2 s, total: 1min 16s
Wall time: 50.4 s


In [106]:
get_nmf_topics(model, vectorizer, 10)

Topic # 01   Topic # 02      Topic # 03   Topic # 04     Topic # 05  \
0  конференция         мозг          пароль    процессор       облачный   
1  выступление      пациент         учётный     смартфон         облако   
2       спикер       клетка  учётный запись           гб         трафик   
3      встреча       учёный     авторизация      ноутбук      провайдер   
4     заказчик      болезнь            флаг      дисплей        сетевой   
5     менеджер  заболевание         задание  аккумулятор       протокол   
6         офис          ген            порт   видеокарта            цод   
7  мероприятие         врач           логин   клавиатура  виртуализация   
8        навык      лечение  аутентификация          чип           шлюз   
9       москва     организм         аккаунт       корпус       заказчик   

            Topic # 06   Topic # 07     Topic # 08              Topic # 09  \
0      порекомендовать  космический     уязвимость                   игрок   
1         предпочитать      спутник          атака                 игровой   
2     профессиональный       орбита  злоумышленник                персонаж   
3              слушать      аппарат    вредоносный                геймплей   
4             бумажный         марс         ботнет                    враг   
5    внутренний проект        земля  исследователь                 комната   
6               музыка      станция     привилегия                  миссия   
7       бумажный книга         наса         угроза                ваш игра   
8  электронный читалка         луна       эксплойт  виртуальный реальность   
9              читалка       ракета         жертва                    жанр   

   Topic # 10     ...                   Topic # 16     Topic # 17  \
0         бот     ...                    нейросеть         лекция   
1         чат     ...                    нейронный        студент   
2    телеграм     ...               нейронный сеть  лекция лекция   
3  мессенджер     ...                    интеллект    университет   
4       токен     ...                     машинный      профессор   
5        лига     ...                искусственный          школа   
6    отправка     ...      искусственный интеллект          слайд   
7     чат бот     ...            машинный обучение      знакомить   
8   текстовый     ...                         слой         монтаж   
9      диалог     ...                       нейрон        понятие   

              Topic # 18            Topic # 19   Topic # 20      Topic # 21  \
0                   диск            сертификат       плагин           товар   
1              резервный                 домен       сборка          скидка   
2                     вм          сертификация        папка         магазин   
3     виртуальный машина         закрытый ключ  репозиторий      покупатель   
4                  бэкап               подпись    контейнер         покупка   
5  резервный копирование            контроллер   директория      распродажа   
6            копирование         открытый ключ         окно           заказ   
7         восстановление                 токен         меню        продавец   
8                кластер              закрытый      каталог           акция   
9                  копия  получение сертификат        релиз  чёрный пятница   

     Topic # 22              Topic # 23  Topic # 24  Topic # 25  
0        печать              автомобиль     реклама    блокчейн  
1       принтер             беспилотный      письмо  финансовый  
2        станок                водитель     контент       банка  
3   температура  беспилотный автомобиль   рекламный      платёж  
4            мм                  дорога    рассылка  транзакция  
5  производство               автопилот   аудитория       доход  
6       пластик                грузовик  социальный       закон  
7       изделие           автомобильный       почта        банк  
8        корпус                   город   подписчик       рубль  
9         плата              

In [107]:
%%time
model, vectorizer = nmf_mod(stexts,n_components=30,ngram_range=(1,2))

CPU times: user 1min 8s, sys: 34.6 s, total: 1min 43s
Wall time: 1min 7s


In [108]:
get_nmf_topics(model, vectorizer, 10)

Topic # 01   Topic # 02  Topic # 03   Topic # 04     Topic # 05  \
0      заказчик       датчик       папка       камера       облачный   
1         рубль  аккумулятор        окно     смартфон         облако   
2      менеджер  температура        меню  регистратор         трафик   
3       стартап   напряжение     вкладка   разрешение      провайдер   
4      директор      батарея      нажать           гб        сетевой   
5  руководитель        плата      панель      дисплей       протокол   
6      зарплата          ток      раздел       съёмка            цод   
7          офис      питание      иконка         кадр  виртуализация   
8       ребёнок      энергия  контроллер        рубль           узел   
9      вакансия       корпус       шрифт     объектив           шлюз   

            Topic # 06   Topic # 07     Topic # 08              Topic # 09  \
0      порекомендовать  космический     уязвимость                   игрок   
1         предпочитать      спутник          атака                 игровой   
2     профессиональный       орбита  злоумышленник                персонаж   
3              слушать      аппарат    вредоносный                    враг   
4    внутренний проект         марс         ботнет                геймплей   
5             бумажный        земля  исследователь                 комната   
6               музыка      станция     привилегия                  миссия   
7       бумажный книга         наса         угроза  виртуальный реальность   
8  электронный читалка         луна         жертва                ваш игра   
9              читалка       ракета       эксплойт              реальность   

   Topic # 10          ...             Topic # 21               Topic # 22  \
0         бот          ...            конференция                нейросеть   
1         чат          ...                 спикер                нейронный   
2    телеграм          ...            выступление           нейронный сеть   
3  мессенджер          ...                 доклад                интеллект   
4       токен          ...                  слайд                 машинный   
5        лига          ...            мероприятие            искусственный   
6    отправка          ...                встреча  искусственный интеллект   
7     чат бот          ...            презентация        машинный обучение   
8      диалог          ...                 москва                     слой   
9   текстовый          ...                декабрь                   нейрон   

               Topic # 23          Topic # 24    Topic # 25    Topic # 26  \
0              автомобиль           процессор      блокчейн        печать   
1             беспилотный                диск    транзакция       принтер   
2                водитель                  гб    финансовый        станок   
3  беспилотный автомобиль             ноутбук         банка       пластик   
4                  дорога          видеокарта      биткойна            мм   
5               автопилот  оперативный память          банк       изделие   
6                грузовик         оперативный  криптовалюта  производство   
7           автомобильный          накопитель        платёж      печатать   
8                   город        жёсткий диск     платёжный         рубль   
9                    авто             жёсткий        валюта        бумага   

   Topic # 27   Topic # 28            Topic # 29             Topic # 30  
0     реклама         мозг            сертификат              резервный  
1      письмо      пациент                 домен                     вм  
2   рекламный       клетка          сертификация                  бэкап  
3     контент       учёный         закрытый ключ  резервный копирование  
4    рассылка      болезнь               подпись     виртуальный машина  
5   аудитория  заболевание         открытый ключ            копирование  
6       домен          ген                 токен         восстановление  
7   подписчик         врач              закрытый      

### 10) в отдельной ячейки напечатайте таблицу с темами лучшей NMF модели, сравните их с теми, что получились в LDA.

Вообще темы получились хорошие везде. Я напечатаю на 20, потому что она точно вся отображается :)

In [110]:
%%time
model, vectorizer = nmf_mod(stexts,n_components=20,ngram_range=(1,2))

CPU times: user 29.5 s, sys: 8.87 s, total: 38.4 s
Wall time: 31.6 s


In [111]:
get_nmf_topics(model, vectorizer, 10)

Topic # 01   Topic # 02   Topic # 03   Topic # 04  Topic # 05  \
0     реклама      пациент       плагин       камера    блокчейн   
1    заказчик         мозг        папка     смартфон  автомобиль   
2    менеджер       клетка       сборка           гб  финансовый   
3   аудитория       учёный  репозиторий  аккумулятор       банка   
4  социальный  заболевание   директория      дисплей      платёж   
5    дизайнер      болезнь    контейнер       корпус       закон   
6      письмо          ген         окно    процессор  транзакция   
7     контент         врач         меню      ноутбук    миллиард   
8   маркетинг      лечение       пароль       датчик        банк   
9     ребёнок     организм      каталог      батарея       доход   

            Topic # 06   Topic # 07     Topic # 08              Topic # 09  \
0      порекомендовать  космический     уязвимость                   игрок   
1         предпочитать      спутник          атака                 игровой   
2     профессиональный       орбита         пароль                персонаж   
3              слушать      аппарат  злоумышленник                    враг   
4               музыка         марс    вредоносный                геймплей   
5             бумажный        земля         ботнет                  миссия   
6    внутренний проект      станция         жертва                 комната   
7       бумажный книга         наса        учётный  виртуальный реальность   
8  электронный читалка         луна     шифрование              реальность   
9              читалка       ракета  исследователь                ваш игра   

   Topic # 10  Topic # 11  Topic # 12  Topic # 13     Topic # 14  Topic # 15  \
0         бот   вселенная      сигнал    анимация          робот      массив   
1         чат   галактика        звук    текстура        ребёнок   указатель   
2    телеграм     энергия     частота     пиксель         датчик  компилятор   
3  мессенджер      звезда     наушник      шейдёр  робототехника    аргумент   
4       токен     материя   усилитель        кадр           дрон  возвращать   
5        лига      тёмный       плата  координата     автомобиль      символ   
6    отправка      солнце    звуковой       сцена         сборка   выражение   
7     чат бот      теория    диапазон      спрайт          школа  анализатор   
8   текстовый   излучение      музыка        слой           узел        байт   
9      диалог  гравитация  напряжение      движок         дронов      индекс   

                Topic # 16      Topic # 17             Topic # 18  \
0                нейросеть           товар                   диск   
1                нейронный          скидка              резервный   
2           нейронный сеть         магазин     виртуальный машина   
3                интеллект      покупатель                     вм   
4                 машинный         покупка                 облако   
5            искусственный      распродажа                кластер   
6  искусственный интеллект           заказ               облачный   
7        машинный обучение           акция            копирование   
8                     слой        продавец                  бэкап   
9                   нейрон  чёрный пятница  резервный копирование   

     Topic # 19   Topic # 20  
0    сертификат  конференция  
1         домен       спикер  
2        письмо  выступление  
3        пароль       доклад  
4      почтовый        слайд  
5         токен  мероприятие  
6        трафик  презентация  
7  сертификация      встреча  
8    контроллер       москва  
9         почта      декабрь

На мой взгляд, результат получился значительно лучше, чем с LDA. Работает быстрее, темы более осмысленные